# APIs

----
# The good stuff

In [273]:
import requests
import pandas as pd

from datetime import datetime

# Sourece to get current Unix Timestamp for the pushshift API:
#  https://stackoverflow.com/questions/16755394/what-is-the-easiest-way-to-get-current-gmt-time-in-unix-timestamp-format
import time

In [276]:
# Sourece to get current Unix Timestamp for the pushshift API:
#  https://stackoverflow.com/questions/16755394/what-is-the-easiest-way-to-get-current-gmt-time-in-unix-timestamp-format
time.time()

1682112833.3211257

In [302]:
def data_getter(subreddit, trials, name):
#=====  INITIAL LOCAL VARIABLES  =================================================================================
    
    # Establish base url:
    url_fnc = 'https://api.pushshift.io/reddit/search/submission'
    
    # Establish initial parameters for most current subreddit pull:
    params_getter = {
    'subreddit': subreddit,
    'size': 1000,
    }
    
    # Create an empty dataframe to which we can concatenate each run
    master_df = pd.DataFrame()
    
#=====  Gathering the data from reddit/pushshift // Create DataFrame // Concatenate to Master  ===================
    
    # Get the data:
    res_fnc = requests.get(url_fnc, params_getter)
    print(res_fnc.status_code) # for debugging
    
    # Make dataframe:
    df = res_fnc.json() # Dump dat to a json
    df = pd.DataFrame(df['data']) # Pull the 'data' dictionary out of the json
    
    # Concatenate to master
    master_df = pd.concat([master_df, df])

#=====  Iterate the above steps over remaining trials  ===========================================================
    for i in range(0, (trials - 1)): # Establishes a for loop to iterate over the remaining trials (minus the first one)
        
        # Update the before parameter to be the retrieved time (in utc) of the last item in the previous trail's dataframe
        params_getter = {
        'subreddit': subreddit,
        'size': 1000,
        'before': list(df['retrieved_utc'][-1:])[0]
        }
        
        # Get the data:
        res_fnc = requests.get(url_fnc, params_getter)
        print(res_fnc.status_code) # for debugging

        # Make dataframe:
        df = res_fnc.json() # Dump dat to a json
        df = pd.DataFrame(df['data']) # Pull the 'data' dictionary out of the json

        # Concatenate to master
        master_df = pd.concat([master_df, df])
    
#=====  Finally, return the fully concatenated master dataframe, reset index, store to csv  =================================================
    master_df.reset_index(drop = True) # Source for refersher on how to tuse this:  https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.reset_index.html
    master_df.to_csv(f'./data/{name}.csv')
    return master_df.head()

In [298]:
data_getter('Showerthoughts', 6, 'showerthoughts')

200
200
200
200
200
200


subreddit   selftext author_fullname  gilded  \
0  Showerthoughts  [removed]     t2_4bc8495k       0   
1  Showerthoughts                 t2_2qefih4       0   
2  Showerthoughts                   t2_ryolf       0   
3  Showerthoughts  [removed]     t2_qfocjje1       0   
4  Showerthoughts                 t2_k1c8aet       0   

                                              title link_flair_richtext  \
0                        Is there life after death?                  []   
1       Elevators must be quite confusing for dogs.                  []   
2  On an animal its a horn. On a plant its a thorn.                  []   
3                                  Serious question                  []   
4              Merry is the bad boy of the hobbits.                  []   

  subreddit_name_prefixed  hidden  pwls link_flair_css_class  ... created_utc  \
0        r/Showerthoughts   False     6                 None  ...  1682115287   
1        r/Showerthoughts   False     6                 None  ...  1682114898   
2        r/Showerthoughts   False     6                 None  ...  1682114865   
3        r/Showerthoughts   False     6                 None  ...  1682114698   
4        r/Showerthoughts   False     6                 None  ...  1682114593   

  num_crossposts  media  is_video retrieved_utc  updated_utc  \
0              0   None     False    1682115303   1682115304   
1              0   None     False    1682114913   1682114913   
2              0   None     False    1682114881   1682114882   
3              0   None     False    1682114713   1682114713   
4              0   None     False    1682114604   1682114604   

      utc_datetime_str post_hint  preview author_cakeday  
0  2023-04-21 22:14:47       NaN      NaN            NaN  
1  2023-04-21 22:08:18       NaN      NaN            NaN  
2  2023-04-21 22:07:45       NaN      NaN            NaN  
3  2023-04-21 22:04:58       NaN      NaN            NaN  
4  2023-04-21 22:03:13       NaN      NaN            NaN  

[5 rows x 89 columns]

In [301]:
data_getter('worldnews', 6, 'worldnews_2')

200
200
200
200
200
200


subreddit selftext author_fullname  gilded  \
0  worldnews                 t2_jr3x2       0   
1  worldnews                 t2_jr3x2       0   
2  worldnews              t2_e53dndri       0   
3  worldnews                t2_11liyr       0   
4  worldnews                 t2_612zd       0   

                                               title  \
0  Biden admin leaning toward evacuating U.S. per...   
1  Biden admin leaning toward evacuating U.S. per...   
2  Help prevent a third world war: Join the Globa...   
3  The Label That Launched Bad Bunny Was Founded ...   
4  Street fighting between the forces of two riva...   

                                 link_flair_richtext subreddit_name_prefixed  \
0                                                 []             r/worldnews   
1                                                 []             r/worldnews   
2  [{'e': 'text', 't': 'Not Appropriate Subreddit'}]             r/worldnews   
3                                                 []             r/worldnews   
4                                                 []             r/worldnews   

   hidden  pwls link_flair_css_class  ...  num_crossposts media  is_video  \
0   False     6                 None  ...               0  None     False   
1   False     6                 None  ...               0  None     False   
2   False     6               normal  ...               0  None     False   
3   False     6                 None  ...               0  None     False   
4   False     6                 None  ...               0  None     False   

   retrieved_utc updated_utc     utc_datetime_str crosspost_parent_list  \
0     1682115285  1682115285  2023-04-21 22:14:33                   NaN   
1     1682115199  1682115199  2023-04-21 22:13:04                   NaN   
2     1682114874  1682114874  2023-04-21 22:07:38                   NaN   
3     1682114392  1682114393  2023-04-21 21:59:36                   NaN   
4     1682114142  1682114143  2023-04-21 21:55:24                   NaN   

  crosspost_parent  author_cakeday link_flair_template_id  
0              NaN             NaN                    NaN  
1              NaN             NaN                    NaN  
2              NaN             NaN                    NaN  
3              NaN             NaN                    NaN  
4              NaN             NaN                    NaN  

[5 rows x 93 columns]

---
# Quick Data Pull Tester
## Run this when not sure if PushShift is Down

In [2]:
url = 'https://api.pushshift.io/reddit/search/submission'

In [270]:
params = {
    'subreddit': 'Showerthoughts',
    'size': 1000,
    'before': list(showerthoughts_5['retrieved_utc'][-1:])[0] # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

200


{'data': [{'subreddit': 'Showerthoughts',
   'selftext': '[removed]',
   'author_fullname': 't2_8rgdm2ekr',
   'gilded': 0,
   'title': 'Evolution is sexist',
   'link_flair_richtext': [],
   'subreddit_name_prefixed': 'r/Showerthoughts',
   'hidden': False,
   'pwls': 6,
   'link_flair_css_class': None,
   'thumbnail_height': None,
   'top_awarded_type': None,
   'hide_score': True,
   'quarantine': False,
   'link_flair_text_color': 'dark',
   'upvote_ratio': 1.0,
   'author_flair_background_color': None,
   'subreddit_type': 'public',
   'total_awards_received': 0,
   'media_embed': {},
   'thumbnail_width': None,
   'author_flair_template_id': None,
   'is_original_content': False,
   'secure_media': None,
   'is_reddit_media_domain': False,
   'is_meta': False,
   'category': None,
   'secure_media_embed': {},
   'link_flair_text': None,
   'score': 1,
   'is_created_from_ads_ui': False,
   'author_premium': False,
   'thumbnail': 'nsfw',
   'edited': False,
   'author_flair_css_c

---
# Abandoned method to get exact count of reddit responses

In [131]:
#  Source inspiring this code:  https://stackoverflow.com/questions/3459098/create-list-of-single-item-repeated-n-times

[999] * 5 + [999]

[999, 999, 999, 999, 999, 999]

In [128]:
n = 10002

runs = [1000]*(n//999) + [n%999+1]
runs

[1000, 1000, 1000, 1000, 1000, 1000, 1000, 1000, 1000, 1000, 13]

In [147]:
dad_jokes_1.tail(1)

subreddit                                      selftext author_fullname  \
998  dadjokes  She's been giving me nothing but cross words     t2_3o6ndc2i   

     gilded                                      title link_flair_richtext  \
998       0  My Sudoku addiction is irritating my wife                  []   

    subreddit_name_prefixed  hidden  pwls link_flair_css_class  ...  \
998              r/dadjokes   False     6                 None  ...   

     retrieved_utc updated_utc     utc_datetime_str  link_flair_template_id  \
998     1681096411  1681096412  2023-04-10 03:13:17                     NaN   

    post_hint  preview crosspost_parent_list url_overridden_by_dest  \
998       NaN      NaN                   NaN                    NaN   

     crosspost_parent author_cakeday  
998               NaN            NaN  

[1 rows x 93 columns]

---
# Fun Trying to Get Duplicates to Work but no Such Luck

In [160]:
d_f = pd.DataFrame({
    'brand': ['Yum Yum', 'Yum Yum', 'Indomie', 'Indomie', 'Indomie'],
    'style': ['cup', 'cup', 'cup', 'pack', 'pack'],
    'rating': [4, 4, 3.5, 15, 5]})
d_f 
#dad_jokes_2.drop_duplicates()

d_f = pd.DataFrame({
    'brand': ['Yum Yum', 'Yum Yam', 'Indomie', 'Indomie', 'Indomie'],
    'style': ['cup', 'cup', 'cup', 'pack', 'pack'],
    'rating': [4, 4, 3.5, 15, 5]})
d_f.drop_duplicates()


dad_jokes_2.drop_duplicates()

TypeError: unhashable type: 'list'

---
# Testing Concatenation to an Empty DataFrame

In [282]:
dummy_df = pd.DataFrame()
dummy_df

new_dad_df = pd.concat([dad_jokes_1, dad_jokes_2])
#new_dad_df.drop_duplicates() # Source:  https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.drop_duplicates.html#pandas.DataFrame.drop_duplicates

#new_dad_df

new_dad_df

subreddit                                  selftext author_fullname  \
0    dadjokes                       Which makes it odd.       t2_16sa6x   
1    dadjokes                 But the music is soulless     t2_81sfkz57   
2    dadjokes                   She broke her calf bone     t2_pjbzysrv   
3    dadjokes  His audience was unresponsive and stiff.    t2_67b2up92p   
4    dadjokes        It's called the Gaga Goo Goo tour.     t2_1i54z8en   
..        ...                                       ...             ...   
994  dadjokes                  Cause he knows is hands.     t2_d3todswa   
995  dadjokes                                 [removed]    t2_7xa9h6k3u   
996  dadjokes         I immediately thought, how dairy.    t2_7gaz1u33s   
997  dadjokes                                Stypticus.     t2_hroo3t49   
998  dadjokes                  They become hummingbirds     t2_4dh189jr   

     gilded                                              title  \
0         0         2 is the only even number that is a prime.   
1         0  A great pianist died in a hotel and people say...   
2         0                   Why did the cow went to the vet?   
3         0  Why did the mortuary assistant feel his jokes ...   
4         0  Did you know Lady Gaga is touring with The Goo...   
..      ...                                                ...   
994       0  Wanna know why I’m scared to fight a deaf person?   
995       0  35[f4M]California states USA looking for a sub...   
996       0  I saw on a bull calf sucking another mother's ...   
997       0  What do you call a gladiator who frequently cu...   
998       0      What happens to birds that can no longer sing   

    link_flair_richtext subreddit_name_prefixed  hidden  pwls  \
0                    []              r/dadjokes   False     6   
1                    []              r/dadjokes   False     6   
2                    []              r/dadjokes   False     6   
3                    []              r/dadjokes   False     6   
4                    []              r/dadjokes   False     6   
..                  ...                     ...     ...   ...   
994                  []              r/dadjokes   False     6   
995                  []              r/dadjokes   False     6   
996                  []              r/dadjokes   False     6   
997                  []              r/dadjokes   False     6   
998                  []              r/dadjokes   False     6   

    link_flair_css_class  ...  retrieved_utc updated_utc     utc_datetime_str  \
0                   None  ...     1681963327  1681963327  2023-04-20 04:01:55   
1                   None  ...     1681962933  1681962934  2023-04-20 03:55:18   
2                   None  ...     1681962873  1681962874  2023-04-20 03:54:23   
3                   None  ...     1681961506  1681961506  2023-04-20 03:31:30   
4                   None  ...     1681960773  1681960773  2023-04-20 03:19:19   
..                   ...  ...            ...         ...                  ...   
994                 None  ...     1680253900  1680253901  2023-03-31 09:11:30   
995                 None  ...     1680253043  1680253043  2023-03-31 08:57:05   
996                 None  ...     1680248682  1680248683  2023-03-31 07:44:32   
997                 None  ...     1680246890  1680246890  2023-03-31 07:14:32   
998                 None  ...     1680246697  1680246698  2023-03-31 07:11:21   

     link_flair_template_id post_hint  preview crosspost_parent_list  \
0                       NaN       NaN      NaN                   NaN   
1                       NaN       NaN      NaN                   NaN   
2                       NaN       NaN      NaN                   NaN   
3                       NaN       NaN      NaN                   NaN   
4                       NaN       NaN      NaN                   NaN   
..                      ...       ...      ...                   ...   
994                     NaN       NaN      NaN      

---
# BRUTE FORCE Pull of DadJokes
## NOTE:  Dates will NOT auto-update like others

In [185]:
params = {
    'subreddit': 'dadjokes',
    'size': 1000,
    #'before': 1681095499 # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}

In [188]:
params = {
    'subreddit': 'dadjokes',
    'size': 1000,
    #'before': 1681095499 # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

dj_1 = res.json()
dj_1 = pd.DataFrame(dj_1['data'])
print(dj_1['retrieved_utc'][-1:])
dj_1

200
999    1681613961
Name: retrieved_utc, dtype: int64


subreddit                                           selftext  \
0    dadjokes                              and never has five...   
1    dadjokes                                          [removed]   
2    dadjokes  Now he has no Monet for Degas to make his Van ...   
3    dadjokes                                          [removed]   
4    dadjokes                                          [removed]   
..        ...                                                ...   
995  dadjokes  He was hit by a Guiness truck! ....credit .......   
996  dadjokes                                          [removed]   
997  dadjokes    They found her Head and Shoulders on the beach.   
998  dadjokes                               I'm nailed right in.   
999  dadjokes                                               wino   

    author_fullname  gilded  \
0          t2_82bsd       0   
1       t2_2uv8l1k3       0   
2          t2_36b5u       0   
3       t2_bk58m0zt       0   
4      t2_7rxg5qy3v       0   
..              ...     ...   
995     t2_vslxf22z       0   
996    t2_6dgk6uzb4       0   
997     t2_vslxf22z       0   
998     t2_lcgdjvry       0   
999     t2_vslxf22z       0   

                                                 title link_flair_richtext  \
0           What has four letters, sometimes has nine,                  []   
1    Did you hear about the fire that broke out dur...                  []   
2    My son decided against my advice to pursue a c...                  []   
3    What do you call a cow with its left side of l...                  []   
4                                                  😋😋😋                  []   
..                                                 ...                 ...   
995                    Twas the drink that killed him.                  []   
996  Why are omelets in France made with only one egg?                  []   
997  They said that woman from the original JAWS mo...                  []   
998  On the top of the cross, what does "INRI" stan...                  []   
999  People ask me all the time if I'm an alcoholic...                  []   

    subreddit_name_prefixed  hidden  pwls link_flair_css_class  ...  \
0                r/dadjokes   False     6                 None  ...   
1                r/dadjokes   False     6                 None  ...   
2                r/dadjokes   False     6                 None  ...   
3                r/dadjokes   False     6                 None  ...   
4                r/dadjokes   False     6                 None  ...   
..                      ...     ...   ...                  ...  ...   
995              r/dadjokes   False     6                 None  ...   
996              r/dadjokes   False     6                 None  ...   
997              r/dadjokes   False     6                 None  ...   
998              r/dadjokes   False     6                 None  ...   
999              r/dadjokes   False     6                 None  ...   

    retrieved_utc updated_utc     utc_datetime_str  post_hint  \
0      1682088057  1682088057  2023-04-21 14:40:39        NaN   
1      1682087774  1682087774  2023-04-21 14:35:57        NaN   
2      1682087668  1682087669  2023-04-21 14:34:11        NaN   
3      1682087332  1682087333  2023-04-21 14:28:38        NaN   
4      1682085802  1682085802  2023-04-21 14:03:05       self   
..            ...         ...                  ...        ...   
995    1681615693  1681615694  2023-04-16 03:27:55        NaN   
996    1681614626  1681614626  2023-04-16 03:10:14        NaN   
997    1681614229  1681614229  2023-04-16 03:03:33        NaN   
998    1681613968  1681613969  2023-04-16 02:59:16        NaN   
999    1681613961  1681613961  2023-04-16 02:59:10        NaN   

                                               preview  \
0                                                  NaN   
1                                                  NaN   
2                                                  NaN   
3          

In [189]:
params = {
    'subreddit': 'dadjokes',
    'size': 1000,
    'before': 1681613961 # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

dj_2 = res.json()
dj_2 = pd.DataFrame(dj_2['data'])
print(dj_2['retrieved_utc'][-1:])
dj_2

200
998    1681162746
Name: retrieved_utc, dtype: int64


subreddit                                selftext author_fullname  gilded  \
0    dadjokes                    I'm nailed right in.     t2_lcgdjvry       0   
1    dadjokes                                    wino     t2_vslxf22z       0   
2    dadjokes             They have a croaking device     t2_7uj6jl4j       0   
3    dadjokes      Why do you need to heat hot water?     t2_vslxf22z       0   
4    dadjokes                  An Italian Suppository     t2_vjcvhkcx       0   
..        ...                                     ...             ...     ...   
994  dadjokes                               [removed]    t2_8yubqihpo       0   
995  dadjokes  Not very neighhhhborly if you ask me 🙄     t2_tc7xxq3m       0   
996  dadjokes              Do they garnish his wages?     t2_jlf9tjwb       0   
997  dadjokes                                             t2_t17s35sl       0   
998  dadjokes                     They make no cents.     t2_7uj6jl4j       0   

                                                 title link_flair_richtext  \
0    On the top of the cross, what does "INRI" stan...                  []   
1    People ask me all the time if I'm an alcoholic...                  []   
2           Why don’t you ever see frogs in Star Trek?                  []   
3              Are hot water heaters really necessary?                  []   
4                     Do you know what an innuendo is?                  []   
..                                                 ...                 ...   
994  دوري أبطال أوروبا (بالإنجليزية: UEFA Champions...                  []   
995  Someone just moved in next door and let their ...                  []   
996  If a parsley farmer is found guilty in a civil...                  []   
997  F 20 chst me up for legit blowjob meetup with ...                  []   
998           Why is it hard to understand volunteers?                  []   

    subreddit_name_prefixed  hidden  pwls link_flair_css_class  ...  \
0                r/dadjokes   False     6                 None  ...   
1                r/dadjokes   False     6                 None  ...   
2                r/dadjokes   False     6                 None  ...   
3                r/dadjokes   False     6                 None  ...   
4                r/dadjokes   False     6                 None  ...   
..                      ...     ...   ...                  ...  ...   
994              r/dadjokes   False     6                 None  ...   
995              r/dadjokes   False     6                 None  ...   
996              r/dadjokes   False     6                 None  ...   
997              r/dadjokes   False     6                 None  ...   
998              r/dadjokes   False     6                 None  ...   

     retrieved_utc updated_utc     utc_datetime_str  link_flair_template_id  \
0       1681613968  1681613969  2023-04-16 02:59:16                     NaN   
1       1681613961  1681613961  2023-04-16 02:59:10                     NaN   
2       1681613635  1681613635  2023-04-16 02:53:45                     NaN   
3       1681612474  1681612474  2023-04-16 02:34:18                     NaN   
4       1681612237  1681612238  2023-04-16 02:30:26                     NaN   
..             ...         ...                  ...                     ...   
994     1681163369  1681163370  2023-04-10 21:49:14                     NaN   
995     1681163202  1681163203  2023-04-10 21:46:25                     NaN   
996     1681163132  1681163132  2023-04-10 21:45:20                     NaN   
997     1681162994  1681162994  2023-04-10 21:43:04                     NaN   
998     1681162746  1681162746  2023-04-10 21:38:50                     NaN   

    post_hint  preview crosspost_parent_list url_overridden_by_dest  \
0         NaN      NaN                   NaN                    NaN   
1         NaN      NaN                   NaN                    NaN   
2         NaN      NaN                   NaN                    NaN   
3       

In [190]:
params = {
    'subreddit': 'dadjokes',
    'size': 1000,
    'before': 1681162746 # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

dj_3 = res.json()
dj_3 = pd.DataFrame(dj_3['data'])
print(dj_3['retrieved_utc'][-1:])
dj_3

200
998    1680719869
Name: retrieved_utc, dtype: int64


subreddit                                           selftext  \
0    dadjokes                                They make no cents.   
1    dadjokes               He got a little behind in his orders   
2    dadjokes                                      From Ovid-19.   
3    dadjokes  In court, the man admitted that he liked it ru...   
4    dadjokes                              He's an in salt comic   
..        ...                                                ...   
994  dadjokes                               My back not hurting.   
995  dadjokes                                          [removed]   
996  dadjokes                  Because they like to stereo-type.   
997  dadjokes                                          [removed]   
998  dadjokes                                          [removed]   

    author_fullname  gilded  \
0       t2_7uj6jl4j       0   
1       t2_5pefyyzk       0   
2       t2_60j60ncl       0   
3       t2_surk3jlh       0   
4       t2_7k8mw59t       0   
..              ...     ...   
994     t2_7uj6jl4j       0   
995    t2_8jc8xyfjl       0   
996        t2_nchdf       0   
997     t2_w6w77ne4       0   
998        t2_fqqgv       0   

                                                 title link_flair_richtext  \
0             Why is it hard to understand volunteers?                  []   
1    Did you hear about the butcher that backed int...                  []   
2                     How did all the Roman poets die?                  []   
3    A local man has just been sent to prison for p...                  []   
4    Did you hear about the comedian who makes fun ...                  []   
..                                                 ...                 ...   
994  My son asked me what my favor childhood memory...                  []   
995                                     Let's GET RICH                  []   
996            Why does the racist have two keyboards?                  []   
997  What does Trump going to jail and reparations ...                  []   
998  I was wondering why it wouldn’t put the lotion...                  []   

    subreddit_name_prefixed  hidden  pwls link_flair_css_class  ...  \
0                r/dadjokes   False     6                 None  ...   
1                r/dadjokes   False     6                 None  ...   
2                r/dadjokes   False     6                 None  ...   
3                r/dadjokes   False     6                 None  ...   
4                r/dadjokes   False     6                 None  ...   
..                      ...     ...   ...                  ...  ...   
994              r/dadjokes   False     6                 None  ...   
995              r/dadjokes   False     6                 None  ...   
996              r/dadjokes   False     6                 None  ...   
997              r/dadjokes   False     6                 None  ...   
998              r/dadjokes   False     6                 None  ...   

     retrieved_utc updated_utc     utc_datetime_str  post_hint preview  \
0       1681162746  1681162746  2023-04-10 21:38:50        NaN     NaN   
1       1681162698  1681162699  2023-04-10 21:38:01        NaN     NaN   
2       1681162618  1681162618  2023-04-10 21:36:46        NaN     NaN   
3       1681162410  1681162411  2023-04-10 21:33:20        NaN     NaN   
4       1681161973  1681161973  2023-04-10 21:26:00        NaN     NaN   
..             ...         ...                  ...        ...     ...   
994     1680720523  1680720523  2023-04-05 18:48:33        NaN     NaN   
995     1680720410  1680720410  2023-04-05 18:46:39        NaN     NaN   
996     1680720265  1680720265  2023-04-05 18:44:09        NaN     NaN   
997     1680719876  1680719877  2023-04-05 18:37:42        NaN     NaN   
998     1680719869  1680719870  2023-04-05 18:37:32        NaN     NaN   

     link_flair_template_id crosspost_parent_list url_overridden_by_dest  \
0                       NaN                   NaN          

In [191]:
params = {
    'subreddit': 'dadjokes',
    'size': 1000,
    'before': 1680719869 # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

dj_4 = res.json()
dj_4 = pd.DataFrame(dj_4['data'])
print(dj_4['retrieved_utc'][-1:])
dj_4

200
999    1680287217
Name: retrieved_utc, dtype: int64


subreddit                                           selftext  \
0    dadjokes                                          [removed]   
1    dadjokes                                          [removed]   
2    dadjokes                                         No raisin.   
3    dadjokes           One part in particular is quite humerus.   
4    dadjokes  ...was asked during a post-match interview, "Y...   
..        ...                                                ...   
995  dadjokes         I told him I have a weekend immune system.   
996  dadjokes                                          [removed]   
997  dadjokes                                         An Alcopop   
998  dadjokes                Cos they'll never cheat on an essay   
999  dadjokes                          They only have one trunk.   

    author_fullname  gilded  \
0       t2_w6w77ne4       0   
1          t2_fqqgv       0   
2       t2_hxysriay       0   
3       t2_1th9m28z       0   
4       t2_ta91j9vt       0   
..              ...     ...   
995     t2_usoqfmhq       0   
996     t2_b8jvltw4       0   
997     t2_8vz0ctne       0   
998     t2_3fij3j2s       0   
999     t2_tqd7sv1t       0   

                                                 title link_flair_richtext  \
0    What does Trump going to jail and reparations ...                  []   
1    I was wondering why it wouldn’t put the lotion...                  []   
2          Green grapes don't talk to red grapes, why?                  []   
3    I have a funny story to share about the human ...                  []   
4    a world famous athlete, known to struggle with...                  []   
..                                                 ...                 ...   
995  My boss asked why I call in sick only on weekd...                  []   
996                When does a joke become a dad-joke?                  []   
997  What do you call a sweet, mildly alcoholic gra...                  []   
998                   Why don't Mexicans use chat gpt?                  []   
999  Why is it hard for elephants to pack for a vac...                  []   

    subreddit_name_prefixed  hidden  pwls link_flair_css_class  ...  \
0                r/dadjokes   False     6                 None  ...   
1                r/dadjokes   False     6                 None  ...   
2                r/dadjokes   False     6                       ...   
3                r/dadjokes   False     6                 None  ...   
4                r/dadjokes   False     6                 None  ...   
..                      ...     ...   ...                  ...  ...   
995              r/dadjokes   False     6                 None  ...   
996              r/dadjokes   False     6                 None  ...   
997              r/dadjokes   False     6                 None  ...   
998              r/dadjokes   False     6                 None  ...   
999              r/dadjokes   False     6                 None  ...   

    retrieved_utc updated_utc     utc_datetime_str  \
0      1680719876  1680719877  2023-04-05 18:37:42   
1      1680719869  1680719870  2023-04-05 18:37:32   
2      1680718905  1680718906  2023-04-05 18:21:34   
3      1680718844  1680718845  2023-04-05 18:20:29   
4      1680718223  1680718223  2023-04-05 18:10:12   
..            ...         ...                  ...   
995    1680288573  1680288574  2023-03-31 18:49:16   
996    1680288000  1680288000  2023-03-31 18:39:44   
997    1680287814  1680287815  2023-03-31 18:36:42   
998    1680287567  1680287568  2023-03-31 18:32:34   
999    1680287217  1680287217  2023-03-31 18:26:44   

                   link_flair_template_id author_cakeday  post_hint preview  \
0                                     NaN            NaN        NaN     NaN   
1                                     NaN            NaN        NaN     NaN   
2    4f7b369a-917a-11ed-b4a4-eecab5b61c69            NaN        NaN     NaN   
3                                     NaN            NaN   

In [192]:
params = {
    'subreddit': 'dadjokes',
    'size': 1000,
    'before': 1680287217 # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

dj_5 = res.json()
dj_5 = pd.DataFrame(dj_5['data'])
print(dj_5['retrieved_utc'][-1:])
dj_5

200
999    1679846793
Name: retrieved_utc, dtype: int64


subreddit                                           selftext  \
0    dadjokes                          They only have one trunk.   
1    dadjokes                                                      
2    dadjokes                                                      
3    dadjokes                                   He Just woke up!   
4    dadjokes  ...Parts A to D are free, but you have to figh...   
..        ...                                                ...   
995  dadjokes                                          [removed]   
996  dadjokes                                                      
997  dadjokes                            You'll get jurasskicked   
998  dadjokes  When my grandfather was ill, my grandmother ru...   
999  dadjokes                 So I bought a steak in his company   

    author_fullname  gilded  \
0       t2_tqd7sv1t       0   
1      t2_880z9weum       0   
2      t2_880z9weum       0   
3       t2_4fl8xo0c       0   
4      t2_6dmnxs2fi       0   
..              ...     ...   
995    t2_5i75o87je       0   
996     t2_c8lu6i27       0   
997      t2_t0ofk2j       0   
998     t2_9asisfig       0   
999        t2_j71dn       0   

                                                 title link_flair_richtext  \
0    Why is it hard for elephants to pack for a vac...                  []   
1    F23 (F4M) I’m down...horny as fuck, ready to d...                  []   
2    F23 (F4M) I’m down...horny as fuck, ready to d...                  []   
3        Did you hear about the kidnapping at the park                  []   
4    I heard the Beastie Boys are releasing a 5 par...                  []   
..                                                 ...                 ...   
995                                            The guy                  []   
996                                     Time Flies....                  []   
997                             Never fight a dinosaur                  []   
998                                     My grandfather                  []   
999        My friend started a successful butcher shop                  []   

    subreddit_name_prefixed  hidden  pwls link_flair_css_class  ...  \
0                r/dadjokes   False     6                 None  ...   
1                r/dadjokes   False     6                 None  ...   
2                r/dadjokes   False     6                 None  ...   
3                r/dadjokes   False     6                 None  ...   
4                r/dadjokes   False     6                 None  ...   
..                      ...     ...   ...                  ...  ...   
995              r/dadjokes   False     6                 None  ...   
996              r/dadjokes   False     6                 None  ...   
997              r/dadjokes   False     6                 None  ...   
998              r/dadjokes   False     6                 None  ...   
999              r/dadjokes   False     6                 None  ...   

    retrieved_utc updated_utc     utc_datetime_str  post_hint preview  \
0      1680287217  1680287217  2023-03-31 18:26:44        NaN     NaN   
1      1680287217  1680287217  2023-03-31 18:26:38        NaN     NaN   
2      1680287060  1680287061  2023-03-31 18:24:04        NaN     NaN   
3      1680286558  1680286558  2023-03-31 18:15:41        NaN     NaN   
4      1680286161  1680286161  2023-03-31 18:09:01        NaN     NaN   
..            ...         ...                  ...        ...     ...   
995    1679847796  1679847797  2023-03-26 16:22:57        NaN     NaN   
996    1679847574  1679847575  2023-03-26 16:19:19        NaN     NaN   
997    1679847276  1679847276  2023-03-26 16:14:25        NaN     NaN   
998    1679847148  1679847148  2023-03-26 16:12:15        NaN     NaN   
999    1679846793  1679846794  2023-03-26 16:06:17        NaN     NaN   

     link_flair_template_id author_cakeday  \
0                       NaN            NaN   
1                       NaN            NaN   
2        

In [193]:
params = {
    'subreddit': 'dadjokes',
    'size': 1000,
    'before': 1679846793 # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

dj_6 = res.json()
dj_6 = pd.DataFrame(dj_6['data'])
print(dj_6['retrieved_utc'][-1:])
dj_6

200
999    1679385881
Name: retrieved_utc, dtype: int64


subreddit                                           selftext  \
0    dadjokes                 So I bought a steak in his company   
1    dadjokes     Just their standard naan disclosure agreement.   
2    dadjokes        "Help, I've fallen and I can't _giddy up_!"   
3    dadjokes  I heard that Reddit was going to run an algori...   
4    dadjokes                                          [removed]   
..        ...                                                ...   
995  dadjokes  A man walks into a coffee shop, and is given a...   
996  dadjokes         Because they don't want to risk their ass.   
997  dadjokes                   Maybe it needs some spring water   
998  dadjokes  I wonder what sound clocks will make if that h...   
999  dadjokes  One says to the other “does this joke seem rig...   

    author_fullname  gilded  \
0          t2_j71dn       0   
1       t2_8uucib2n       0   
2       t2_bhb2fvvn       0   
3       t2_cpam55np       0   
4       t2_97nosjz5       0   
..              ...     ...   
995     t2_lw7m0u4e       0   
996     t2_v9wmbafz       0   
997     t2_2o7jx737       0   
998     t2_7i7q0k35       0   
999     t2_ec2ijtjc       0   

                                                 title link_flair_richtext  \
0          My friend started a successful butcher shop                  []   
1    The Indian restaurant I work for is so secreti...                  []   
2                 What did the horse say when it fell?                  []   
3                        Reddit Joke Duplicate Purge?!                  []   
4                  Have you ever tried to catch a FOG?                  []   
..                                                 ...                 ...   
995                  A man walks into a coffee shop...                  []   
996                Why people don't like the asterisk?                  []   
997               My waterbed just ain't bouncy enough                  []   
998  Did you guys hear TikTok will probably get ban...                  []   
999             Two clowns are eating a cannibal’s leg                  []   

    subreddit_name_prefixed  hidden  pwls link_flair_css_class  ...  \
0                r/dadjokes   False     6                 None  ...   
1                r/dadjokes   False     6                 None  ...   
2                r/dadjokes   False     6                 None  ...   
3                r/dadjokes   False     6                 None  ...   
4                r/dadjokes   False     6                 None  ...   
..                      ...     ...   ...                  ...  ...   
995              r/dadjokes   False     6                 None  ...   
996              r/dadjokes   False     6                 None  ...   
997              r/dadjokes   False     6                 None  ...   
998              r/dadjokes   False     6                 None  ...   
999              r/dadjokes   False     6                 None  ...   

    retrieved_utc updated_utc     utc_datetime_str  post_hint preview  \
0      1679846793  1679846794  2023-03-26 16:06:17        NaN     NaN   
1      1679846649  1679846650  2023-03-26 16:03:53        NaN     NaN   
2      1679845870  1679845871  2023-03-26 15:50:50        NaN     NaN   
3      1679845621  1679845621  2023-03-26 15:46:43        NaN     NaN   
4      1679845144  1679845144  2023-03-26 15:38:46        NaN     NaN   
..            ...         ...                  ...        ...     ...   
995    1679394200  1679394200  2023-03-21 10:23:08        NaN     NaN   
996    1679390703  1679390704  2023-03-21 09:24:52        NaN     NaN   
997    1679389589  1679389589  2023-03-21 09:06:14        NaN     NaN   
998    1679386733  1679386734  2023-03-21 08:18:32        NaN     NaN   
999    1679385881  1679385881  2023-03-21 08:04:25        NaN     NaN   

     link_flair_template_id author_cakeday crosspost_parent_list  \
0                       NaN            NaN                   NaN   
1          

In [194]:
dj_1.to_csv('./data/dj_1.csv')
dj_2.to_csv('./data/dj_2.csv')
dj_3.to_csv('./data/dj_3.csv')
dj_4.to_csv('./data/dj_4.csv')
dj_5.to_csv('./data/dj_5.csv')
dj_6.to_csv('./data/dj_6.csv')

---
# BRUTE FORCE Pull of NotTheOnion
## NOTE:  Dates will NOT auto-update like others

In [195]:
params = {
    'subreddit': 'nottheonion',
    'size': 1000,
    #'before': 1679846793 # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

nto_1 = res.json()
nto_1 = pd.DataFrame(nto_1['data'])
print(nto_1['retrieved_utc'][-1:])
nto_1.to_csv('./data/nto_1.csv')
nto_1

200
999    1681412443
Name: retrieved_utc, dtype: int64


subreddit                   selftext  gilded  \
0    nottheonion                                  0   
1    nottheonion                                  0   
2    nottheonion                                  0   
3    nottheonion                                  0   
4    nottheonion                                  0   
..           ...                        ...     ...   
995  nottheonion                                  0   
996  nottheonion                                  0   
997  nottheonion                                  0   
998  nottheonion                                  0   
999  nottheonion  Sounds like Charlie work.       0   

                                                 title link_flair_richtext  \
0    OFFICIAL - The appeal against the disqualifica...                  []   
1    Russian plane accidentally strikes Russian cit...                  []   
2                   Gooch holds early lead at LIV Golf                  []   
3    A woman gets 21 years for trying to kill her d...                  []   
4    A woman gets 21 years for trying to kill her d...                  []   
..                                                 ...                 ...   
995  Male chess player disguises himself as woman, ...                  []   
996  TIL scientists from Newcastle University disco...                  []   
997  Beverly Grove area business owner says 'nude h...                  []   
998  Beverly Grove area business owner says 'nude h...                  []   
999                                 NYC hires rat czar                  []   

    subreddit_name_prefixed  hidden  pwls link_flair_css_class  \
0             r/nottheonion   False     6                 None   
1             r/nottheonion   False     6                 None   
2             r/nottheonion   False     6                 None   
3             r/nottheonion   False     6                 None   
4             r/nottheonion   False     6                 None   
..                      ...     ...   ...                  ...   
995           r/nottheonion   False     6                 None   
996           r/nottheonion   False     6                 None   
997           r/nottheonion   False     6                 None   
998           r/nottheonion   False     6                 None   
999           r/nottheonion   False     6                 None   

     thumbnail_height  ...                                                url  \
0               134.0  ...  https://twitter.com/marifcinter/status/1649374...   
1                73.0  ...  https://www.theguardian.com/world/2023/apr/21/...   
2                78.0  ...  https://www.espn.com/golf/story/_/id/36252156/...   
3                78.0  ...  https://www.npr.org/2023/04/21/1171083112/russ...   
4                78.0  ...  https://www.npr.org/2023/04/21/1171083112/russ...   
..                ...  ...                                                ...   
995              78.0  ...  https://www.chess.com/news/view/cheating-kenya...   
996              78.0  ...  https://www.abc.net.au/news/2011-06-03/shaken-...   
997               NaN  ...  https://abc7.com/amp/nude-homeless-encampment-...   
998              78.0  ...  https://abc7.com/nude-homeless-encampment-site...   
999              93.0  ...  https://apnews.com/article/rat-czar-new-york-m...   

     subreddit_subscribers  created_utc num_crossposts  \
0                 22184086   1682088681              0   
1                 22184072   1682088407              0   
2                 22184054   1682087442              0   
3                 22183990   1682085437              0   
4                 22183962   1682084724              0   
..                     ...          ...            ...   
995               22167907   1681413514              0   
996               22167907   1681413406              0   
997               22167905   1681413371              0   
998               22167870   1681412589              0   
999  

In [196]:
params = {
    'subreddit': 'nottheonion',
    'size': 1000,
    'before': 1681412443 # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

nto_2 = res.json()
nto_2 = pd.DataFrame(nto_2['data'])
print(nto_2['retrieved_utc'][-1:])
nto_2.to_csv('./data/nto_2.csv')
nto_2.head()

200
999    1680546998
Name: retrieved_utc, dtype: int64


subreddit                   selftext author_fullname  gilded  \
0  nottheonion  Sounds like Charlie work.     t2_5xbpxw2u       0   
1  nottheonion                                t2_5xbpxw2u       0   
2  nottheonion                                   t2_xjsan       0   
3  nottheonion                                 t2_btqmgc3       0   
4  nottheonion                                t2_9wb1xpxf       0   

                                               title link_flair_richtext  \
0                                 NYC hires rat czar                  []   
1                          Sounds like Charlie work.                  []   
2  Sheriff under scrutiny for handling of guns at...                  []   
3  Police complaint against a dog for tearing a p...                  []   
4  Federal Judge Throws 'Science Under the Bus' W...                  []   

  subreddit_name_prefixed  hidden  pwls link_flair_css_class  ...  \
0           r/nottheonion   False     6                 None  ...   
1           r/nottheonion   False     6                 None  ...   
2           r/nottheonion   False     6                 None  ...   
3           r/nottheonion   False     6                 None  ...   
4           r/nottheonion   False     6                 None  ...   

   created_utc num_crossposts  media  is_video retrieved_utc  updated_utc  \
0   1681412432              0   None     False    1681412443   1681412444   
1   1681412068              0   None     False    1681412082   1681412082   
2   1681411825              0   None     False    1681411837   1681411838   
3   1681410663              0   None     False    1681410675   1681410675   
4   1681410609              0   None     False    1681410629   1681410630   

      utc_datetime_str                              crosspost_parent_list  \
0  2023-04-13 19:00:32                                                NaN   
1  2023-04-13 18:54:28                                                NaN   
2  2023-04-13 18:50:25                                                NaN   
3  2023-04-13 18:31:03                                                NaN   
4  2023-04-13 18:30:09  [{'approved_at_utc': None, 'subreddit': 'polit...   

   crosspost_parent author_cakeday  
0               NaN            NaN  
1               NaN            NaN  
2               NaN            NaN  
3               NaN            NaN  
4        t3_12kkkpl            NaN  

[5 rows x 92 columns]

In [197]:
params = {
    'subreddit': 'nottheonion',
    'size': 1000,
    'before': 1680546998 # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

nto_3 = res.json()
nto_3 = pd.DataFrame(nto_3['data'])
print(nto_3['retrieved_utc'][-1:])
nto_3.to_csv('./data/nto_3.csv')
nto_3.head()

200
997    1679755039
Name: retrieved_utc, dtype: int64


subreddit selftext author_fullname  gilded  \
0  nottheonion               t2_lh10xit       0   
1  nottheonion                 t2_5ya1c       0   
2  nottheonion              t2_3r0mw058       0   
3  nottheonion              t2_rg2w2ftz       0   
4  nottheonion                 t2_c8pez       0   

                                               title link_flair_richtext  \
0  Suella Braverman claims £25,000 to pay househo...                  []   
1  Superintendent candidate says job offer was re...                  []   
2  ‘Moana’ Live-Action Remake Set at Disney With ...                  []   
3  Florida School Censors Madonna and Child; Call...                  []   
4  PM's official residence closed following disco...                  []   

  subreddit_name_prefixed  hidden  pwls link_flair_css_class  ...  \
0           r/nottheonion   False     6                 None  ...   
1           r/nottheonion   False     6                 None  ...   
2           r/nottheonion   False     6                 None  ...   
3           r/nottheonion   False     6                 None  ...   
4           r/nottheonion   False     6                 None  ...   

   created_utc num_crossposts  media  is_video retrieved_utc  updated_utc  \
0   1680546979              0   None     False    1680546998   1680546999   
1   1680546809              0   None     False    1680546825   1680546826   
2   1680546013              0   None     False    1680546027   1680546028   
3   1680544075              0   None     False    1680544089   1680544090   
4   1680543959              0   None     False    1680543970   1680543970   

      utc_datetime_str crosspost_parent_list  crosspost_parent author_cakeday  
0  2023-04-03 18:36:19                   NaN               NaN            NaN  
1  2023-04-03 18:33:29                   NaN               NaN            NaN  
2  2023-04-03 18:20:13                   NaN               NaN            NaN  
3  2023-04-03 17:47:55                   NaN               NaN            NaN  
4  2023-04-03 17:45:59                   NaN               NaN            NaN  

[5 rows x 92 columns]

In [199]:
nto_3.shape

(998, 92)

In [200]:
params = {
    'subreddit': 'nottheonion',
    'size': 1000,
    'before': 1679755039 # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

nto_4 = res.json()
nto_4 = pd.DataFrame(nto_4['data'])
print(nto_4['retrieved_utc'][-1:])
nto_4.to_csv('./data/nto_4.csv')
nto_4.head()

200
998    1678849947
Name: retrieved_utc, dtype: int64


subreddit selftext author_fullname  gilded  \
0  nottheonion                t2_13l44z       0   
1  nottheonion              t2_4d921nch       0   
2  nottheonion              t2_3wg6elyq       0   
3  nottheonion              t2_ai1alne6       0   
4  nottheonion              t2_4d921nch       0   

                                               title link_flair_richtext  \
0  Kanye West says he's no longer an anti-semite ...                  []   
1  Kanye West: Jonah Hill ‘Made Me Like Jewish Pe...                  []   
2  Lauren Boebert Says She Wants To Abolish the D...                  []   
3  Principal resigns after Florida students shown...                  []   
4  Kanye West Says Jonah Hill in '21 Jump Street'...                  []   

  subreddit_name_prefixed  hidden  pwls link_flair_css_class  ...  \
0           r/nottheonion   False     6                 None  ...   
1           r/nottheonion   False     6                 None  ...   
2           r/nottheonion   False     6                 None  ...   
3           r/nottheonion   False     6                 None  ...   
4           r/nottheonion   False     6                 None  ...   

   created_utc num_crossposts  media  is_video retrieved_utc  updated_utc  \
0   1679755026              0   None     False    1679755039   1679755039   
1   1679754990              0   None     False    1679755000   1679755001   
2   1679754069              0   None     False    1679754086   1679754087   
3   1679753717              0   None     False    1679753734   1679753734   
4   1679753573              0   None     False    1679753591   1679753591   

      utc_datetime_str                              crosspost_parent_list  \
0  2023-03-25 14:37:06                                                NaN   
1  2023-03-25 14:36:30                                                NaN   
2  2023-03-25 14:21:09  [{'approved_at_utc': None, 'subreddit': 'polit...   
3  2023-03-25 14:15:17                                                NaN   
4  2023-03-25 14:12:53                                                NaN   

   crosspost_parent author_cakeday  
0               NaN            NaN  
1               NaN            NaN  
2        t3_121kdld            NaN  
3               NaN            NaN  
4               NaN            NaN  

[5 rows x 92 columns]

In [203]:
params = {
    'subreddit': 'nottheonion',
    'size': 1000,
    'before': 1678849947 # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

nto_5 = res.json()
nto_5 = pd.DataFrame(nto_5['data'])
print(nto_5['retrieved_utc'][-1:])
nto_5.to_csv('./data/nto_5.csv')
nto_5.head()

200
999    1678145389
Name: retrieved_utc, dtype: int64


subreddit selftext author_fullname  gilded  \
0  nottheonion              t2_8d4j6vl0       0   
1  nottheonion                 t2_r9hiu       0   
2  nottheonion              t2_4td2aypy       0   
3  nottheonion              t2_4c5k4e8g       0   
4  nottheonion              t2_4c5k4e8g       0   

                                               title link_flair_richtext  \
0  National Park Service warns not to push your '...                  []   
1  Don’t buy animals from breeders in parking lot...                  []   
2  Kentucky middle school principal arrested firs...                  []   
3  GOP state legislator opposed to free school lu...                  []   
4  GOP state legislature opposed free school lunc...                  []   

  subreddit_name_prefixed  hidden  pwls link_flair_css_class  ...  \
0           r/nottheonion   False     6                 None  ...   
1           r/nottheonion   False     6                 None  ...   
2           r/nottheonion   False     6                 None  ...   
3           r/nottheonion   False     6                 None  ...   
4           r/nottheonion   False     6                 None  ...   

                                               media is_video  retrieved_utc  \
0                                               None    False     1678849947   
1                                               None    False     1678849084   
2                                               None    False     1678847097   
3                                               None    False     1678846945   
4  {'type': 'twitter.com', 'oembed': {'provider_u...    False     1678846863   

   updated_utc     utc_datetime_str  post_hint  \
0   1678892459  2023-03-15 03:12:10        NaN   
1   1678892459  2023-03-15 02:57:51       link   
2   1678892451  2023-03-15 02:24:44       link   
3   1678892446  2023-03-15 02:22:12       link   
4   1678892446  2023-03-15 02:20:49       link   

                                             preview crosspost_parent_list  \
0                                                NaN                   NaN   
1  {'images': [{'source': {'url': 'https://extern...                   NaN   
2  {'images': [{'source': {'url': 'https://extern...                   NaN   
3  {'images': [{'source': {'url': 'https://extern...                   NaN   
4  {'images': [{'source': {'url': 'https://extern...                   NaN   

   crosspost_parent author_cakeday  
0               NaN            NaN  
1               NaN            NaN  
2               NaN            NaN  
3               NaN            NaN  
4               NaN            NaN  

[5 rows x 92 columns]

In [204]:
params = {
    'subreddit': 'nottheonion',
    'size': 1000,
    'before': 1678145389 # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

nto_6 = res.json()
nto_6 = pd.DataFrame(nto_6['data'])
print(nto_6['retrieved_utc'][-1:])
nto_6.to_csv('./data/nto_6.csv')
nto_6.head()

200
999    1677396486
Name: retrieved_utc, dtype: int64


subreddit selftext author_fullname  gilded  \
0  nottheonion              t2_ratn6kot       0   
1  nottheonion              t2_36a1faqk       0   
2  nottheonion              t2_h8yeqpuk       0   
3  nottheonion               t2_zlm1st6       0   
4  nottheonion              t2_6ixdmwzg       0   

                                               title link_flair_richtext  \
0  SF Tech Couple Marries in Taco Bell ‘Metaverse...                  []   
1  San Francisco to House its Homeless Population...                  []   
2  We’re heading into a world where a flat-screen...                  []   
3  Anime actress encourages fans to bathe before ...                  []   
4  "Alt-right" women are upset that "alt-right" m...                  []   

  subreddit_name_prefixed  hidden  pwls link_flair_css_class  ...  \
0           r/nottheonion   False     6                 None  ...   
1           r/nottheonion   False     6                 None  ...   
2           r/nottheonion   False     6                 None  ...   
3           r/nottheonion   False     6                 None  ...   
4           r/nottheonion   False     6                 None  ...   

   num_crossposts media  is_video  retrieved_utc updated_utc  \
0               0  None     False     1678145389  1678145390   
1               0  None     False     1678143759  1678143759   
2               0  None     False     1678143633  1678143633   
3               0  None     False     1678141727  1678141728   
4               0  None     False     1678140343  1678140343   

      utc_datetime_str                              crosspost_parent_list  \
0  2023-03-06 23:29:38                                                NaN   
1  2023-03-06 23:02:26  [{'approved_at_utc': None, 'subreddit': 'Crypt...   
2  2023-03-06 23:00:19                                                NaN   
3  2023-03-06 22:28:34                                                NaN   
4  2023-03-06 22:05:28  [{'approved_at_utc': None, 'subreddit': 'TwoXC...   

  crosspost_parent  author_cakeday link_flair_template_id  
0              NaN             NaN                    NaN  
1       t3_11k0929             NaN                    NaN  
2              NaN             NaN                    NaN  
3              NaN             NaN                    NaN  
4       t3_11jzbfr             NaN                    NaN  

[5 rows x 93 columns]

---
# BRUTE FORCE Pull of AskDocs
## NOTE:  Dates will NOT auto-update like others

In [198]:
params = {
    'subreddit': 'AskDocs',
    'size': 1000,
    #'before': 1680546998 # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

askdocs_1 = res.json()
askdocs_1 = pd.DataFrame(askdocs_1['data'])
print(askdocs_1['retrieved_utc'][-1:])
askdocs_1.to_csv('./data/askdocs_1.csv')
askdocs_1.head()

200
999    1681961372
Name: retrieved_utc, dtype: int64


subreddit                                           selftext  \
0   AskDocs  I am 20F. Just been in hospital for hyperphost...   
1   AskDocs  I have a large blister on the end of my index ...   
2   AskDocs                                          [removed]   
3   AskDocs  33 male \n5’9\n185 LBS\nMale\n\nRecently went ...   
4   AskDocs  19M 6ft1 142lbs White \n\nSo I've been having ...   

  author_fullname  gilded                                              title  \
0     t2_lj32g4i2       0  Severe pain in lower back now I can’t pee prop...   
1     t2_fdez5u2j       0  Large burn blister on dominant hands index fin...   
2        t2_gfhb8       0                                Chronic Pelvic Pain   
3     t2_967w6cqb       0                              CBC with Differential   
4      t2_hq4nxzs       0  Lower abdomen discomfort and constipation with...   

  link_flair_richtext subreddit_name_prefixed  hidden  pwls  \
0                  []               r/AskDocs   False     6   
1                  []               r/AskDocs   False     6   
2                  []               r/AskDocs   False     6   
3                  []               r/AskDocs   False     6   
4                  []               r/AskDocs   False     6   

  link_flair_css_class  ... created_utc num_crossposts  media  is_video  \
0                 None  ...  1682089333              0   None     False   
1                 None  ...  1682089326              0   None     False   
2                 None  ...  1682089286              0   None     False   
3                 None  ...  1682089284              0   None     False   
4                 None  ...  1682089185              0   None     False   

  retrieved_utc  updated_utc     utc_datetime_str post_hint  preview  \
0    1682089351   1682089351  2023-04-21 15:02:13       NaN      NaN   
1    1682089341   1682089341  2023-04-21 15:02:06       NaN      NaN   
2    1682089302   1682089303  2023-04-21 15:01:26       NaN      NaN   
3    1682089302   1682089303  2023-04-21 15:01:24       NaN      NaN   
4    1682089200   1682089201  2023-04-21 14:59:45       NaN      NaN   

  author_cakeday  
0            NaN  
1            NaN  
2            NaN  
3            NaN  
4            NaN  

[5 rows x 89 columns]

In [205]:
params = {
    'subreddit': 'AskDocs',
    'size': 1000,
    'before': 1681961372 # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

askdocs_2 = res.json()
askdocs_2 = pd.DataFrame(askdocs_2['data'])
print(askdocs_2['retrieved_utc'][-1:])
askdocs_2.to_csv('./data/askdocs_2.csv')
askdocs_2.head()

200
997    1681860994
Name: retrieved_utc, dtype: int64


subreddit                                           selftext  \
0   AskDocs  20F, 5’1, 120 lbs. \n\nYesterday morning I not...   
1   AskDocs                                          [removed]   
2   AskDocs  Hi there,\n\n(M30) Starting last Thursday (4/1...   
3   AskDocs  19F. Is this a pimple, a rash or a bug bite? F...   
4   AskDocs  Hey all. This is a weird one.\n\nI'm a male in...   

  author_fullname  gilded                                              title  \
0     t2_k4ozfkx2       0           Itchy, pus-filled spot on arm + numbness   
1    t2_9i7slekh8       0  Could this be a false positive or the result o...   
2       t2_11ou58       0  Pain around left kidney when I cough and lower...   
3     t2_4uuci65q       0                                      What is this?   
4        t2_h3sbf       0  Found a suture on my sphincter from 15 years a...   

  link_flair_richtext subreddit_name_prefixed  hidden  pwls  \
0                  []               r/AskDocs   False     6   
1                  []               r/AskDocs   False     6   
2                  []               r/AskDocs   False     6   
3                  []               r/AskDocs   False     6   
4                  []               r/AskDocs   False     6   

  link_flair_css_class  ... created_utc num_crossposts  media  is_video  \
0                 None  ...  1681961359              0   None     False   
1                 None  ...  1681961358              0   None     False   
2                 None  ...  1681961349              0   None     False   
3                 None  ...  1681961301              0   None     False   
4                 None  ...  1681961177              0   None     False   

  retrieved_utc  updated_utc     utc_datetime_str post_hint  \
0    1681961372   1681961373  2023-04-20 03:29:19       NaN   
1    1681961372   1681961373  2023-04-20 03:29:18       NaN   
2    1681961365   1681961365  2023-04-20 03:29:09       NaN   
3    1681961313   1681961313  2023-04-20 03:28:21      self   
4    1681961191   1681961192  2023-04-20 03:26:17       NaN   

                                             preview author_cakeday  
0                                                NaN            NaN  
1                                                NaN            NaN  
2                                                NaN            NaN  
3  {'images': [{'source': {'url': 'https://extern...            NaN  
4                                                NaN            NaN  

[5 rows x 89 columns]

In [206]:
params = {
    'subreddit': 'AskDocs',
    'size': 1000,
    'before': 1681860994 # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

askdocs_3 = res.json()
askdocs_3 = pd.DataFrame(askdocs_3['data'])
print(askdocs_3['retrieved_utc'][-1:])
askdocs_3.to_csv('./data/askdocs_3.csv')
askdocs_3.head()

200
999    1681760500
Name: retrieved_utc, dtype: int64


subreddit                                           selftext  \
0   AskDocs  I have do a weekly intramuscular injection, an...   
1   AskDocs                                          [removed]   
2   AskDocs                                          [removed]   
3   AskDocs  Short history: Began manifesting as what felt ...   
4   AskDocs  \n\nHello, I (23M) had a flu about 2 months be...   

  author_fullname  gilded                                              title  \
0     t2_2n01fsku       0    19M, Lump formed immediately after IM injection   
1     t2_njmx1wf8       0  sore tongue and under area of tongue with no a...   
2     t2_2n01fsku       0         Lump formed immediately after IM injection   
3     t2_eo7be351       0  23M, 170lbs, 5'10. Healthy - physio question, ...   
4    t2_8irc8lmay       0  How to cure continuous cough that affects my s...   

  link_flair_richtext subreddit_name_prefixed  hidden  pwls  \
0                  []               r/AskDocs   False     6   
1                  []               r/AskDocs   False     6   
2                  []               r/AskDocs   False     6   
3                  []               r/AskDocs   False     6   
4                  []               r/AskDocs   False     6   

  link_flair_css_class  ... created_utc num_crossposts  media  is_video  \
0                 None  ...  1681860980              0   None     False   
1                 None  ...  1681860977              0   None     False   
2                 None  ...  1681860854              0   None     False   
3                 None  ...  1681860764              0   None     False   
4                 None  ...  1681860737              0   None     False   

  retrieved_utc  updated_utc     utc_datetime_str post_hint  preview  \
0    1681860994   1681860995  2023-04-18 23:36:20       NaN      NaN   
1    1681860987   1681860987  2023-04-18 23:36:17       NaN      NaN   
2    1681860870   1681860870  2023-04-18 23:34:14       NaN      NaN   
3    1681860775   1681860776  2023-04-18 23:32:44       NaN      NaN   
4    1681860752   1681860752  2023-04-18 23:32:17       NaN      NaN   

  author_cakeday  
0            NaN  
1            NaN  
2            NaN  
3            NaN  
4            NaN  

[5 rows x 89 columns]

In [207]:
params = {
    'subreddit': 'AskDocs',
    'size': 1000,
    'before': 1681760500 # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

askdocs_4 = res.json()
askdocs_4 = pd.DataFrame(askdocs_4['data'])
print(askdocs_4['retrieved_utc'][-1:])
askdocs_4.to_csv('./data/askdocs_4.csv')
askdocs_4.head()

200
998    1681650957
Name: retrieved_utc, dtype: int64


subreddit                                           selftext  \
0   AskDocs  I had a close friend (30M) suddenly go into ca...   
1   AskDocs  4 days ago I popped myself into grade 4 hemorr...   
2   AskDocs                                          [removed]   
3   AskDocs  I was prescribed a 5 day course (500mg twice a...   
4   AskDocs  Hello! \nI’m very thankful to find out this su...   

  author_fullname  gilded                                              title  \
0     t2_h8h2a9v4       0  what is the "weird feeling" people have before...   
1     t2_2fga5vu7       0            Is grade 4 hemorrhoids a life sentence?   
2     t2_du4b49p1       0                                              Bumps   
3     t2_85pnmdpb       0  Short of breath after taking one tab of Ciprof...   
4     t2_pik7s5we       0           Chest Discomfort and Shortness of Breath   

  link_flair_richtext subreddit_name_prefixed  hidden  pwls  \
0                  []               r/AskDocs   False     6   
1                  []               r/AskDocs   False     6   
2                  []               r/AskDocs   False     6   
3                  []               r/AskDocs   False     6   
4                  []               r/AskDocs   False     6   

  link_flair_css_class  ... created_utc num_crossposts  media  is_video  \
0                 None  ...  1681760484              0   None     False   
1                 None  ...  1681760242              0   None     False   
2                 None  ...  1681760223              0   None     False   
3                 None  ...  1681760132              0   None     False   
4                 None  ...  1681760034              0   None     False   

  retrieved_utc  updated_utc     utc_datetime_str post_hint  preview  \
0    1681760500   1681760500  2023-04-17 19:41:24       NaN      NaN   
1    1681760253   1681760253  2023-04-17 19:37:22       NaN      NaN   
2    1681760235   1681760236  2023-04-17 19:37:03       NaN      NaN   
3    1681760149   1681760150  2023-04-17 19:35:32       NaN      NaN   
4    1681760052   1681760053  2023-04-17 19:33:54       NaN      NaN   

  author_cakeday  
0            NaN  
1            NaN  
2            NaN  
3            NaN  
4            NaN  

[5 rows x 89 columns]

In [209]:
params = {
    'subreddit': 'AskDocs',
    'size': 1000,
    'before': 1681650957 # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

askdocs_5 = res.json()
askdocs_5 = pd.DataFrame(askdocs_5['data'])
print(askdocs_5['retrieved_utc'][-1:])
askdocs_5.to_csv('./data/askdocs_5.csv')
askdocs_5.head()

200
999    1681531343
Name: retrieved_utc, dtype: int64


subreddit                                           selftext  \
0   AskDocs  I’m 24, female and had my first daughter in De...   
1   AskDocs  [weight: 67kg, height: 5’6] I was suffering fr...   
2   AskDocs  32F, 106lbs, childhood allergy to cephaclor, c...   
3   AskDocs                                          [removed]   
4   AskDocs  Hello, I've been having moderate cough with wh...   

  author_fullname  gilded                                              title  \
0    t2_6pexs0f1t       0                                    Extreme fatigue   
1     t2_67is9gkp       0  I[25F] have 43x42mm endometriotic cyst in righ...   
2     t2_dv4i791v       0           16 days post c section incision bleeding   
3    t2_97mzy93ka       0                   A dumb question but just curious   
4     t2_3ijb0q5r       0          16M, having a cough for the past 2 months   

  link_flair_richtext subreddit_name_prefixed  hidden  pwls  \
0                  []               r/AskDocs   False     6   
1                  []               r/AskDocs   False     6   
2                  []               r/AskDocs   False     6   
3                  []               r/AskDocs   False     6   
4                  []               r/AskDocs   False     6   

  link_flair_css_class  ... created_utc num_crossposts  media  is_video  \
0                 None  ...  1681650943              0   None     False   
1                 None  ...  1681650849              0   None     False   
2                 None  ...  1681650833              0   None     False   
3                 None  ...  1681650783              0   None     False   
4                 None  ...  1681650683              0   None     False   

  retrieved_utc  updated_utc     utc_datetime_str post_hint  preview  \
0    1681650957   1681650958  2023-04-16 13:15:43       NaN      NaN   
1    1681650862   1681650862  2023-04-16 13:14:09       NaN      NaN   
2    1681650853   1681650853  2023-04-16 13:13:53       NaN      NaN   
3    1681650798   1681650798  2023-04-16 13:13:03       NaN      NaN   
4    1681650696   1681650697  2023-04-16 13:11:23       NaN      NaN   

  author_cakeday  
0            NaN  
1            NaN  
2            NaN  
3            NaN  
4            NaN  

[5 rows x 89 columns]

In [229]:
list(askdocs_6['retrieved_utc'][-1:])[0]

1681433256

In [210]:
params = {
    'subreddit': 'AskDocs',
    'size': 1000,
    'before': 1681531343 # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

askdocs_6 = res.json()
askdocs_6 = pd.DataFrame(askdocs_6['data'])
print(askdocs_6['retrieved_utc'][-1:])
askdocs_6.to_csv('./data/askdocs_6.csv')
askdocs_6.head()

200
998    1681433256
Name: retrieved_utc, dtype: int64


subreddit                                           selftext  \
0   AskDocs  I (28F, 150 pounds) had secondary amenorrhea f...   
1   AskDocs  almost 18 years old, nonbinary, white, slavic,...   
2   AskDocs  30yo female, 140 pounds, 5’7. Confirmed PVC’s ...   
3   AskDocs  24 m, white, 190 lbs,  asthma, depression, anx...   
4   AskDocs  \nI, F20, 160cm,50kg had a serious UTI infecti...   

  author_fullname  gilded                                              title  \
0     t2_b60k3ug7       0  Bleeding two weeks after my period - should I ...   
1     t2_ve5tgx6y       0  waking up tired and with a headache, along wit...   
2     t2_kb45fod2       0      Can taking a ppi cause PVC’s in some people ?   
3       t2_16owlv       0  Prednisone for asthma helping hr, bp, appetite...   
4     t2_4nefh0ke       0  What does my lab test results mean? Why am I r...   

  link_flair_richtext subreddit_name_prefixed  hidden  pwls  \
0                  []               r/AskDocs   False     6   
1                  []               r/AskDocs   False     6   
2                  []               r/AskDocs   False     6   
3                  []               r/AskDocs   False     6   
4                  []               r/AskDocs   False     6   

  link_flair_css_class  ... created_utc num_crossposts  media  is_video  \
0                 None  ...  1681531331              0   None     False   
1                 None  ...  1681531320              0   None     False   
2                 None  ...  1681531302              0   None     False   
3                 None  ...  1681531147              0   None     False   
4                 None  ...  1681531080              0   None     False   

  retrieved_utc  updated_utc     utc_datetime_str post_hint  preview  \
0    1681531343   1681531344  2023-04-15 04:02:11       NaN      NaN   
1    1681531336   1681531337  2023-04-15 04:02:00       NaN      NaN   
2    1681531313   1681531314  2023-04-15 04:01:42       NaN      NaN   
3    1681531163   1681531163  2023-04-15 03:59:07       NaN      NaN   
4    1681531094   1681531095  2023-04-15 03:58:00       NaN      NaN   

  author_cakeday  
0            NaN  
1            NaN  
2            NaN  
3            NaN  
4            NaN  

[5 rows x 89 columns]

---
# BRUTE FORCE Pull of WorldNews
## NOTE:  Dates WILL auto-update!!!

In [236]:
params = {
    'subreddit': 'worldnews',
    'size': 1000,
    #'before': 1681531343 # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

worldnews_1 = res.json()
worldnews_1 = pd.DataFrame(worldnews_1['data'])
print(worldnews_1['retrieved_utc'][-1:])
worldnews_1.to_csv('./data/worldnews_1.csv')
worldnews_1.head()

200
998    1681828316
Name: retrieved_utc, dtype: int64


subreddit selftext author_fullname  gilded  \
0  worldnews              t2_i2na0u9g       0   
1  worldnews              t2_5e5w08dj       0   
2  worldnews              t2_jd7pp86k       0   
3  worldnews              t2_7xhn0f18       0   
4  worldnews              t2_jm0h6jj3       0   

                                               title  \
0  Russia's air force accidentally bombs own city...   
1     Japan GSDF Confirms Death of 8th Division Head   
2  16-Year-Old Iranian Kurdish girl Hasti Hossein...   
3  “The Secret to Europe’s Rapid Progression: Unv...   
4  Weather tracker: heat in Spain could smash Apr...   

                      link_flair_richtext subreddit_name_prefixed  hidden  \
0  [{'e': 'text', 't': 'Russia/Ukraine'}]             r/worldnews   False   
1                                      []             r/worldnews   False   
2                                      []             r/worldnews   False   
3                                      []             r/worldnews   False   
4                                      []             r/worldnews   False   

   pwls link_flair_css_class  ...  num_crossposts media  is_video  \
0     6               russia  ...               0  None     False   
1     6                 None  ...               0  None     False   
2     6                 None  ...               0  None     False   
3     6                 None  ...               0  None     False   
4     6                 None  ...               0  None     False   

   retrieved_utc updated_utc     utc_datetime_str  \
0     1682090467  1682090468  2023-04-21 15:20:53   
1     1682090381  1682090381  2023-04-21 15:19:25   
2     1682090242  1682090242  2023-04-21 15:17:03   
3     1682089952  1682089952  2023-04-21 15:12:16   
4     1682089855  1682089856  2023-04-21 15:10:43   

                               crosspost_parent_list crosspost_parent  \
0                                                NaN              NaN   
1  [{'approved_at_utc': None, 'subreddit': 'news'...       t3_12u6man   
2  [{'approved_at_utc': None, 'subreddit': 'NewIr...       t3_12trgw3   
3                                                NaN              NaN   
4                                                NaN              NaN   

   author_cakeday link_flair_template_id  
0             NaN                    NaN  
1             NaN                    NaN  
2             NaN                    NaN  
3             NaN                    NaN  
4             NaN                    NaN  

[5 rows x 93 columns]

In [237]:
params = {
    'subreddit': 'worldnews',
    'size': 1000,
    'before': list(worldnews_1['retrieved_utc'][-1:])[0] # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

worldnews_2 = res.json()
worldnews_2 = pd.DataFrame(worldnews_2['data'])
print(worldnews_2['retrieved_utc'][-1:])
worldnews_2.to_csv('./data/worldnews_2.csv')
worldnews_2.head()

200
997    1681537101
Name: retrieved_utc, dtype: int64


subreddit selftext author_fullname  gilded  \
0  worldnews              t2_vn2u3b5m       0   
1  worldnews              t2_tg1ieqhk       0   
2  worldnews              t2_5z4hzvd5       0   
3  worldnews              t2_uwoeokx3       0   
4  worldnews              t2_vld7gkdk       0   

                                               title  \
0  Intersecting northern light, a mysterious Gala...   
1  Russia pulls mothballed Cold War-era tanks out...   
2  Japan's population drops by half a million in ...   
3  Scientists Accidentally Discovered New Materia...   
4  'Not Real': Artist Refuses Photography Award A...   

                      link_flair_richtext subreddit_name_prefixed  hidden  \
0                                      []             r/worldnews   False   
1  [{'e': 'text', 't': 'Russia/Ukraine'}]             r/worldnews   False   
2                                      []             r/worldnews   False   
3                                      []             r/worldnews   False   
4                                      []             r/worldnews   False   

   pwls link_flair_css_class  ...  created_utc num_crossposts  media  \
0     6                 None  ...   1681828298              0   None   
1     6               russia  ...   1681828295              0   None   
2     6                 None  ...   1681828172              0   None   
3     6                 None  ...   1681827766              0   None   
4     6                 None  ...   1681827673              0   None   

   is_video retrieved_utc  updated_utc     utc_datetime_str  \
0     False    1681828316   1681828316  2023-04-18 14:31:38   
1     False    1681828308   1681828308  2023-04-18 14:31:35   
2     False    1681828188   1681828188  2023-04-18 14:29:32   
3     False    1681827780   1681827781  2023-04-18 14:22:46   
4     False    1681827690   1681827691  2023-04-18 14:21:13   

  crosspost_parent_list  crosspost_parent link_flair_template_id  
0                   NaN               NaN                    NaN  
1                   NaN               NaN                    NaN  
2                   NaN               NaN                    NaN  
3                   NaN               NaN                    NaN  
4                   NaN               NaN                    NaN  

[5 rows x 92 columns]

In [238]:
params = {
    'subreddit': 'worldnews',
    'size': 1000,
    'before': list(worldnews_2['retrieved_utc'][-1:])[0] # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

worldnews_3 = res.json()
worldnews_3 = pd.DataFrame(worldnews_3['data'])
print(worldnews_3['retrieved_utc'][-1:])
worldnews_3.to_csv('./data/worldnews_3.csv')
worldnews_3.head()

200
999    1681278644
Name: retrieved_utc, dtype: int64


subreddit selftext author_fullname  gilded  \
0  worldnews                 t2_9ci31       0   
1  worldnews             t2_99i75hc22       0   
2  worldnews              t2_w88x9v9t       0   
3  worldnews                 t2_5wds8       0   
4  worldnews                t2_174cr0       0   

                                               title  \
0  Tibetans Explain What ‘Suck My Tongue’ Means. ...   
1  Japan PM Fumio Kishida evacuated after what ap...   
2  JPMorgan Chase profits jump 52% amid banking t...   
3  ‘Something special’: same-sex couple wed in UK...   
4  Iran's hardline government executed at least 5...   

                      link_flair_richtext subreddit_name_prefixed  hidden  \
0                                      []             r/worldnews   False   
1                                      []             r/worldnews   False   
2                                      []             r/worldnews   False   
3  [{'e': 'text', 't': 'Russia/Ukraine'}]             r/worldnews   False   
4                                      []             r/worldnews   False   

   pwls link_flair_css_class  ...  subreddit_subscribers created_utc  \
0     6                 None  ...               31447459  1681537090   
1     6                 None  ...               31447438  1681536469   
2     6                 None  ...               31447429  1681536320   
3     6               russia  ...               31447411  1681535969   
4     6                 None  ...               31447363  1681535360   

   num_crossposts  media is_video  retrieved_utc updated_utc  \
0               0   None    False     1681537101  1681537101   
1               0   None    False     1681536481  1681536481   
2               0   None    False     1681536334  1681536334   
3               0   None    False     1681535981  1681535982   
4               0   None    False     1681535372  1681535372   

      utc_datetime_str  crosspost_parent_list crosspost_parent  
0  2023-04-15 05:38:10                    NaN              NaN  
1  2023-04-15 05:27:49                    NaN              NaN  
2  2023-04-15 05:25:20                    NaN              NaN  
3  2023-04-15 05:19:29                    NaN              NaN  
4  2023-04-15 05:09:20                    NaN              NaN  

[5 rows x 91 columns]

In [239]:
params = {
    'subreddit': 'worldnews',
    'size': 1000,
    'before': list(worldnews_3['retrieved_utc'][-1:])[0] # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

worldnews_4 = res.json()
worldnews_4 = pd.DataFrame(worldnews_4['data'])
print(worldnews_4['retrieved_utc'][-1:])
worldnews_4.to_csv('./data/worldnews_4.csv')
worldnews_4.head()

200
993    1680976927
Name: retrieved_utc, dtype: int64


subreddit selftext author_fullname  gilded  \
0  worldnews              t2_jy3lj1tv       0   
1  worldnews              t2_90uq6p5q       0   
2  worldnews              t2_9jdrnuui       0   
3  worldnews             t2_8xa790l6o       0   
4  worldnews              t2_htnnhgct       0   

                                               title  \
0  India says Ukraine requesting medicines, medic...   
1  Iran exploits quake relief mission to fly weap...   
2                   World Studies EE Data Collection   
3              MAKE $8 PER MINUTE TYPING ON CAPTCHAs   
4  Hong Kong spends HK$1.3 million on YouTube vid...   

                           link_flair_richtext subreddit_name_prefixed  \
0       [{'e': 'text', 't': 'Russia/Ukraine'}]             r/worldnews   
1                                           []             r/worldnews   
2                                           []             r/worldnews   
3            [{'e': 'text', 't': 'No videos'}]             r/worldnews   
4  [{'e': 'text', 't': 'Behind Soft Paywall'}]             r/worldnews   

   hidden  pwls link_flair_css_class  ...  created_utc num_crossposts  \
0   False     6               russia  ...   1681278633              0   
1   False     6                 None  ...   1681278072              0   
2   False     6                 None  ...   1681276932              0   
3   False     6               normal  ...   1681276888              0   
4   False     6          softpaywall  ...   1681276431              0   

                                               media  is_video retrieved_utc  \
0                                               None     False    1681278644   
1                                               None     False    1681278084   
2                                               None     False    1681276950   
3  {'type': 'youtube.com', 'oembed': {'provider_u...     False    1681276898   
4                                               None     False    1681276449   

   updated_utc     utc_datetime_str crosspost_parent_list  crosspost_parent  \
0   1681278644  2023-04-12 05:50:33                   NaN               NaN   
1   1681278084  2023-04-12 05:41:12                   NaN               NaN   
2   1681276951  2023-04-12 05:22:12                   NaN               NaN   
3   1681276899  2023-04-12 05:21:28                   NaN               NaN   
4   1681276449  2023-04-12 05:13:51                   NaN               NaN   

  author_cakeday  
0            NaN  
1            NaN  
2            NaN  
3            NaN  
4            NaN  

[5 rows x 92 columns]

In [240]:
params = {
    'subreddit': 'worldnews',
    'size': 1000,
    'before': list(worldnews_4['retrieved_utc'][-1:])[0] # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

worldnews_5 = res.json()
worldnews_5 = pd.DataFrame(worldnews_5['data'])
print(worldnews_5['retrieved_utc'][-1:])
worldnews_5.to_csv('./data/worldnews_5.csv')
worldnews_5.head()

200
998    1680713049
Name: retrieved_utc, dtype: int64


subreddit selftext author_fullname  gilded  \
0  worldnews              t2_6a5dfaol       0   
1  worldnews              t2_6a5dfaol       0   
2  worldnews              t2_ah8sa6qq       0   
3  worldnews             t2_5p4ybij3e       0   
4  worldnews             t2_5p4ybij3e       0   

                                               title  \
0  As the Ukraine war grinds on, the EU finds it ...   
1  Fuels from Russian oil gets backdoor entry int...   
2  Saudi officials arrive in Iran to discuss reop...   
3  Google and Amazon are struggling to lay off wo...   
4  FBI warns of for-profit companies targeting se...   

                      link_flair_richtext subreddit_name_prefixed  hidden  \
0  [{'e': 'text', 't': 'Russia/Ukraine'}]             r/worldnews   False   
1  [{'e': 'text', 't': 'Russia/Ukraine'}]             r/worldnews   False   
2                                      []             r/worldnews   False   
3                                      []             r/worldnews   False   
4                                      []             r/worldnews   False   

   pwls link_flair_css_class  ...  media is_video  retrieved_utc  updated_utc  \
0     6               russia  ...   None    False     1680976927   1680976927   
1     6               russia  ...   None    False     1680976598   1680976598   
2     6                 None  ...   None    False     1680976391   1680976392   
3     6                 None  ...   None    False     1680976257   1680976258   
4     6                 None  ...   None    False     1680976041   1680976042   

      utc_datetime_str  post_hint  \
0  2023-04-08 18:01:34        NaN   
1  2023-04-08 17:56:27       link   
2  2023-04-08 17:52:58       link   
3  2023-04-08 17:50:41       link   
4  2023-04-08 17:47:05        NaN   

                                             preview crosspost_parent_list  \
0                                                NaN                   NaN   
1  {'images': [{'source': {'url': 'https://extern...                   NaN   
2  {'images': [{'source': {'url': 'https://extern...                   NaN   
3  {'images': [{'source': {'url': 'https://extern...                   NaN   
4                                                NaN                   NaN   

   crosspost_parent author_cakeday  
0               NaN            NaN  
1               NaN            NaN  
2               NaN            NaN  
3               NaN            NaN  
4               NaN            NaN  

[5 rows x 92 columns]

In [241]:
params = {
    'subreddit': 'worldnews',
    'size': 1000,
    'before': list(worldnews_5['retrieved_utc'][-1:])[0] # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

worldnews_6 = res.json()
worldnews_6 = pd.DataFrame(worldnews_6['data'])
print(worldnews_6['retrieved_utc'][-1:])
worldnews_6.to_csv('./data/worldnews_6.csv')
worldnews_6.head()

200
998    1680461095
Name: retrieved_utc, dtype: int64


subreddit selftext author_fullname  gilded  \
0  worldnews             t2_51o32flg0       0   
1  worldnews              t2_e6p8a5x0       0   
2  worldnews             t2_51o32flg0       0   
3  worldnews             t2_68kgnryup       0   
4  worldnews              t2_w69u0g12       0   

                                               title  \
0             Turkey compares Sweden to Nazi Germany   
1  The United States Has Given Ukraine All The He...   
2            Turkiet jämför Sverige med Nazityskland   
3            Canadian at the Airport Busted for Weed   
4  Putin: West helped Ukraine mount acts of sabotage   

                      link_flair_richtext subreddit_name_prefixed  hidden  \
0                                      []             r/worldnews   False   
1  [{'e': 'text', 't': 'Russia/Ukraine'}]             r/worldnews   False   
2                                      []             r/worldnews   False   
3                                      []             r/worldnews   False   
4  [{'e': 'text', 't': 'Russia/Ukraine'}]             r/worldnews   False   

   pwls link_flair_css_class  ...  subreddit_subscribers created_utc  \
0     6                 None  ...               31386673  1680713030   
1     6               russia  ...               31386674  1680713025   
2     6                 None  ...               31386671  1680712996   
3     6                 None  ...               31386636  1680712491   
4     6               russia  ...               31386616  1680712251   

   num_crossposts  media is_video  retrieved_utc updated_utc  \
0               0   None    False     1680713049  1680713049   
1               0   None    False     1680713040  1680713040   
2               0   None    False     1680713007  1680713008   
3               0   None    False     1680712502  1680712503   
4               0   None    False     1680712264  1680712265   

      utc_datetime_str  crosspost_parent_list crosspost_parent  
0  2023-04-05 16:43:50                    NaN              NaN  
1  2023-04-05 16:43:45                    NaN              NaN  
2  2023-04-05 16:43:16                    NaN              NaN  
3  2023-04-05 16:34:51                    NaN              NaN  
4  2023-04-05 16:30:51                    NaN              NaN  

[5 rows x 91 columns]

---
# BRUTE FORCE Pull of ShowerThoughts
## NOTE:  Dates WILL auto-update!!!

In [242]:
params = {
    'subreddit': 'Showerthoughts',
    'size': 1000,
    #'before': list(worldnews_5['retrieved_utc'][-1:])[0] # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

showerthoughts_1 = res.json()
showerthoughts_1 = pd.DataFrame(showerthoughts_1['data'])
print(showerthoughts_1['retrieved_utc'][-1:])
showerthoughts_1.to_csv('./data/showerthoughts_1.csv')
showerthoughts_1.head()

200
997    1681941783
Name: retrieved_utc, dtype: int64


subreddit                                           selftext  \
0  Showerthoughts                                                      
1  Showerthoughts                                                      
2  Showerthoughts                                                      
3  Showerthoughts                                                      
4  Showerthoughts  Both have possible positive outcomes, but you’...   

  author_fullname  gilded                                              title  \
0     t2_1766ep9q       0  The most annoying thing about popcorn is getti...   
1     t2_9bzjxc5b       0  The declining interest in flower pressing like...   
2     t2_55jtxbch       0  What if oxygen has a distinct taste but we've ...   
3      t2_nsqgnwy       0  The US is a place where businesses now offer 4...   
4      t2_o8190av       0  Pushing for a low paying job to pay you higher...   

  link_flair_richtext subreddit_name_prefixed  hidden  pwls  \
0                  []        r/Showerthoughts   False     6   
1                  []        r/Showerthoughts   False     6   
2                  []        r/Showerthoughts   False     6   
3                  []        r/Showerthoughts   False     6   
4                  []        r/Showerthoughts   False     6   

  link_flair_css_class  ... created_utc num_crossposts  media  is_video  \
0                 None  ...  1682091080              0   None     False   
1                 None  ...  1682091055              0   None     False   
2                 None  ...  1682090805              0   None     False   
3                 None  ...  1682090776              0   None     False   
4                 None  ...  1682090747              0   None     False   

  retrieved_utc  updated_utc     utc_datetime_str author_cakeday  post_hint  \
0    1682091101   1682091101  2023-04-21 15:31:20            NaN        NaN   
1    1682091069   1682091070  2023-04-21 15:30:55            NaN        NaN   
2    1682090828   1682090829  2023-04-21 15:26:45            NaN        NaN   
3    1682090789   1682090790  2023-04-21 15:26:16            NaN        NaN   
4    1682090769   1682090770  2023-04-21 15:25:47            NaN        NaN   

  preview  
0     NaN  
1     NaN  
2     NaN  
3     NaN  
4     NaN  

[5 rows x 89 columns]

In [243]:
params = {
    'subreddit': 'Showerthoughts',
    'size': 1000,
    'before': list(showerthoughts_1['retrieved_utc'][-1:])[0] # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

showerthoughts_2 = res.json()
showerthoughts_2 = pd.DataFrame(showerthoughts_2['data'])
print(showerthoughts_2['retrieved_utc'][-1:])
showerthoughts_2.to_csv('./data/showerthoughts_2.csv')
showerthoughts_2.head()

200
996    1681793873
Name: retrieved_utc, dtype: int64


subreddit   selftext author_fullname  gilded  \
0  Showerthoughts                t2_2jf7o1pz       0   
1  Showerthoughts  [removed]     t2_a3uliqwx       0   
2  Showerthoughts                t2_8nvi5q98       0   
3  Showerthoughts                t2_2jf7o1pz       0   
4  Showerthoughts                   t2_hww18       0   

                                               title link_flair_richtext  \
0  Mum's moan about people leaving the toilet sea...                  []   
1  On each “history/celebration of x month” you c...                  []   
2  You never can be in a empty room, you can only...                  []   
3  Mums moan at Sons for leaving the toilet seat ...                  []   
4  If you're particularly proud of a password you...                  []   

  subreddit_name_prefixed  hidden  pwls link_flair_css_class  ... created_utc  \
0        r/Showerthoughts   False     6                 None  ...  1681941771   
1        r/Showerthoughts   False     6                 None  ...  1681941727   
2        r/Showerthoughts   False     6                 None  ...  1681941673   
3        r/Showerthoughts   False     6                 None  ...  1681941650   
4        r/Showerthoughts   False     6                 None  ...  1681941464   

  num_crossposts  media  is_video retrieved_utc  updated_utc  \
0              0   None     False    1681941783   1681941784   
1              0   None     False    1681941743   1681941744   
2              0   None     False    1681941688   1681941689   
3              0   None     False    1681941664   1681941665   
4              0   None     False    1681941482   1681941483   

      utc_datetime_str author_cakeday  post_hint preview  
0  2023-04-19 22:02:51            NaN        NaN     NaN  
1  2023-04-19 22:02:07            NaN        NaN     NaN  
2  2023-04-19 22:01:13            NaN        NaN     NaN  
3  2023-04-19 22:00:50            NaN        NaN     NaN  
4  2023-04-19 21:57:44            NaN        NaN     NaN  

[5 rows x 89 columns]

In [244]:
params = {
    'subreddit': 'Showerthoughts',
    'size': 1000,
    'before': list(showerthoughts_2['retrieved_utc'][-1:])[0] # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

showerthoughts_3 = res.json()
showerthoughts_3 = pd.DataFrame(showerthoughts_3['data'])
print(showerthoughts_3['retrieved_utc'][-1:])
showerthoughts_3.to_csv('./data/showerthoughts_3.csv')
showerthoughts_3.head()

200
999    1681654222
Name: retrieved_utc, dtype: int64


subreddit   selftext author_fullname  gilded  \
0  Showerthoughts                t2_3b4ig5y2       0   
1  Showerthoughts                t2_8h7yboby       0   
2  Showerthoughts  [removed]     t2_uq7rja9d       0   
3  Showerthoughts  [removed]     t2_1a6gtoqx       0   
4  Showerthoughts                t2_ahg690xt       0   

                                               title link_flair_richtext  \
0  Since we are all inevitably going to die, we a...                  []   
1  What if Jesus’s disciples were queer and that’...                  []   
2                                    Shower thoughts                  []   
3               Woke ideologues are just race incels                  []   
4  We kidnap dogs and then they fall in love with...                  []   

  subreddit_name_prefixed  hidden  pwls link_flair_css_class  ... created_utc  \
0        r/Showerthoughts   False     6                 None  ...  1681793859   
1        r/Showerthoughts   False     6                 None  ...  1681793806   
2        r/Showerthoughts   False     6                 None  ...  1681793294   
3        r/Showerthoughts   False     6                 None  ...  1681792807   
4        r/Showerthoughts   False     6                 None  ...  1681792788   

  num_crossposts  media  is_video retrieved_utc  updated_utc  \
0              0   None     False    1681793873   1681793874   
1              0   None     False    1681793820   1681793821   
2              0   None     False    1681793313   1681793313   
3              0   None     False    1681792819   1681792819   
4              0   None     False    1681792804   1681792805   

      utc_datetime_str author_cakeday  post_hint preview  
0  2023-04-18 04:57:39            NaN        NaN     NaN  
1  2023-04-18 04:56:46            NaN        NaN     NaN  
2  2023-04-18 04:48:14            NaN        NaN     NaN  
3  2023-04-18 04:40:07            NaN        NaN     NaN  
4  2023-04-18 04:39:48            NaN        NaN     NaN  

[5 rows x 89 columns]

In [246]:
params = {
    'subreddit': 'Showerthoughts',
    'size': 1000,
    'before': list(showerthoughts_3['retrieved_utc'][-1:])[0] # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

showerthoughts_4 = res.json()
showerthoughts_4 = pd.DataFrame(showerthoughts_4['data'])
print(showerthoughts_4['retrieved_utc'][-1:])
showerthoughts_4.to_csv('./data/showerthoughts_4.csv')
showerthoughts_4.head()

200
998    1681390749
Name: retrieved_utc, dtype: int64


subreddit   selftext author_fullname  gilded  \
0  Showerthoughts  [removed]      t2_136d55e       0   
1  Showerthoughts                t2_pa76w3ml       0   
2  Showerthoughts                   t2_3ev21       0   
3  Showerthoughts                t2_doqlcnvj       0   
4  Showerthoughts  [deleted]             NaN       0   

                                               title link_flair_richtext  \
0  Why does competitive chess have separate male ...                  []   
1  How dose the world have debt like who is it ow...                  []   
2  Hulu Hogan might be the most financially succe...                  []   
3  If soap smells good but tastes horrible...how ...                  []   
4  Hulu Hogan might be the most financially succe...                  []   

  subreddit_name_prefixed  hidden  pwls link_flair_css_class  ... created_utc  \
0        r/Showerthoughts   False     6                 None  ...  1681516578   
1        r/Showerthoughts   False     6                 None  ...  1681516339   
2        r/Showerthoughts   False     6                 None  ...  1681516287   
3        r/Showerthoughts   False     6                 None  ...  1681516259   
4        r/Showerthoughts   False     6                 None  ...  1681516248   

  num_crossposts  media  is_video retrieved_utc  updated_utc  \
0              0   None     False    1681516593   1681516593   
1              0   None     False    1681516354   1681516354   
2              0   None     False    1681516298   1681516298   
3              0   None     False    1681516274   1681516275   
4              0   None     False    1681516266   1681516267   

      utc_datetime_str post_hint  preview author_cakeday  
0  2023-04-14 23:56:18       NaN      NaN            NaN  
1  2023-04-14 23:52:19       NaN      NaN            NaN  
2  2023-04-14 23:51:27       NaN      NaN            NaN  
3  2023-04-14 23:50:59       NaN      NaN            NaN  
4  2023-04-14 23:50:48       NaN      NaN            NaN  

[5 rows x 89 columns]

In [247]:
params = {
    'subreddit': 'Showerthoughts',
    'size': 1000,
    'before': list(showerthoughts_4['retrieved_utc'][-1:])[0] # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

showerthoughts_5 = res.json()
showerthoughts_5 = pd.DataFrame(showerthoughts_5['data'])
print(showerthoughts_5['retrieved_utc'][-1:])
showerthoughts_5.to_csv('./data/showerthoughts_5.csv')
showerthoughts_5.head()

200
999    1681243124
Name: retrieved_utc, dtype: int64


subreddit   selftext author_fullname  gilded  \
0  Showerthoughts               t2_8i5bl58oe       0   
1  Showerthoughts                t2_aiana0ll       0   
2  Showerthoughts  [removed]     t2_a153k7fq       0   
3  Showerthoughts                   t2_tep6m       0   
4  Showerthoughts                   t2_iv3hk       0   

                                               title link_flair_richtext  \
0  Tacos are so versatile they can be eaten as br...                  []   
1                          All advice is life advice                  []   
2  Humans knowing that their ancestors evolved Pa...                  []   
3  Bodyguards should be called peopleguards. If t...                  []   
4  Was John Hancock the Donald J. Trump of his time?                  []   

  subreddit_name_prefixed  hidden  pwls link_flair_css_class  ... created_utc  \
0        r/Showerthoughts   False     6                 None  ...  1681390738   
1        r/Showerthoughts   False     6                 None  ...  1681390729   
2        r/Showerthoughts   False     6                 None  ...  1681390673   
3        r/Showerthoughts   False     6                 None  ...  1681390562   
4        r/Showerthoughts   False     6                 None  ...  1681390557   

  num_crossposts  media  is_video retrieved_utc  updated_utc  \
0              0   None     False    1681390749   1681390750   
1              0   None     False    1681390742   1681390742   
2              0   None     False    1681390685   1681390686   
3              0   None     False    1681390575   1681390576   
4              0   None     False    1681390567   1681390568   

      utc_datetime_str post_hint  preview author_cakeday  
0  2023-04-13 12:58:58       NaN      NaN            NaN  
1  2023-04-13 12:58:49       NaN      NaN            NaN  
2  2023-04-13 12:57:53       NaN      NaN            NaN  
3  2023-04-13 12:56:02       NaN      NaN            NaN  
4  2023-04-13 12:55:57       NaN      NaN            NaN  

[5 rows x 89 columns]

In [248]:
params = {
    'subreddit': 'Showerthoughts',
    'size': 1000,
    'before': list(showerthoughts_5['retrieved_utc'][-1:])[0] # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

showerthoughts_6 = res.json()
showerthoughts_6 = pd.DataFrame(showerthoughts_6['data'])
print(showerthoughts_6['retrieved_utc'][-1:])
showerthoughts_6.to_csv('./data/showerthoughts_6.csv')
showerthoughts_6.head()

200
999    1681085017
Name: retrieved_utc, dtype: int64


subreddit   selftext author_fullname  gilded  \
0  Showerthoughts  [removed]    t2_8rgdm2ekr       0   
1  Showerthoughts                t2_csus59h3       0   
2  Showerthoughts                t2_dxers7m0       0   
3  Showerthoughts                t2_csus59h3       0   
4  Showerthoughts  [removed]        t2_5ztrh       0   

                                               title link_flair_richtext  \
0                                Evolution is sexist                  []   
1    Has anyone actually gone broke by going 'woke'?                  []   
2  Teenagers brag about how expensive their thing...                  []   
3  Why is the phrase 'go woke, go broke' a thing ...                  []   
4  if one plus one is equal to two ones its two b...                  []   

  subreddit_name_prefixed  hidden  pwls link_flair_css_class  ... created_utc  \
0        r/Showerthoughts   False     6                 None  ...  1681243110   
1        r/Showerthoughts   False     6                 None  ...  1681242932   
2        r/Showerthoughts   False     6                 None  ...  1681242881   
3        r/Showerthoughts   False     6                 None  ...  1681242837   
4        r/Showerthoughts   False     6                 None  ...  1681242809   

  num_crossposts  media  is_video retrieved_utc  updated_utc  \
0              0   None     False    1681243124   1681243125   
1              0   None     False    1681242943   1681242944   
2              0   None     False    1681242894   1681242895   
3              0   None     False    1681242854   1681242855   
4              0   None     False    1681242821   1681242822   

      utc_datetime_str post_hint  preview author_cakeday  
0  2023-04-11 19:58:30       NaN      NaN            NaN  
1  2023-04-11 19:55:32       NaN      NaN            NaN  
2  2023-04-11 19:54:41       NaN      NaN            NaN  
3  2023-04-11 19:53:57       NaN      NaN            NaN  
4  2023-04-11 19:53:29       NaN      NaN            NaN  

[5 rows x 89 columns]

---
# BRUTE FORCE Pull of TheOnion
## NOTE:  Dates WILL auto-update!!!

In [249]:
params = {
    'subreddit': 'TheOnion',
    'size': 1000,
    #'before': list(worldnews_5['retrieved_utc'][-1:])[0] # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

theonion_1 = res.json()
theonion_1 = pd.DataFrame(theonion_1['data'])
print(theonion_1['retrieved_utc'][-1:])
theonion_1.to_csv('./data/theonion_1.csv')
theonion_1.head()

200
999    1673228054
Name: retrieved_utc, dtype: int64


subreddit selftext author_fullname  gilded  \
0  TheOnion              t2_dm9dhddc       0   
1  TheOnion                 t2_3jamc       0   
2  TheOnion                 t2_3jamc       0   
3  TheOnion                 t2_3jamc       0   
4  TheOnion                 t2_3jamc       0   

                                               title link_flair_richtext  \
0  USDA Just Doing Quick Smell Tests To Inspect A...                  []   
1  Bachelorette Party Spends Combined $6,000 To E...                  []   
2  Chaperones Instructed To Turn Away Any Student...                  []   
3  ‘Your Father Would Be So Proud Of You,’ Says M...                  []   
4  Republican Voters Explain Their Top Issues For...                  []   

  subreddit_name_prefixed  hidden  pwls link_flair_css_class  ...  \
0              r/TheOnion   False     6                 None  ...   
1              r/TheOnion   False     6                 None  ...   
2              r/TheOnion   False     6                 None  ...   
3              r/TheOnion   False     6                 None  ...   
4              r/TheOnion   False     6                 None  ...   

   retrieved_utc updated_utc     utc_datetime_str  is_gallery media_metadata  \
0     1682089515  1682089515  2023-04-21 15:05:02         NaN            NaN   
1     1682075094  1682075095  2023-04-21 11:04:42         NaN            NaN   
2     1682073433  1682073433  2023-04-21 10:37:02         NaN            NaN   
3     1682072561  1682072562  2023-04-21 10:22:26         NaN            NaN   
4     1682071460  1682071461  2023-04-21 10:04:05         NaN            NaN   

   gallery_data crosspost_parent_list crosspost_parent  author_created_utc  \
0           NaN                   NaN              NaN                 NaN   
1           NaN                   NaN              NaN                 NaN   
2           NaN                   NaN              NaN                 NaN   
3           NaN                   NaN              NaN                 NaN   
4           NaN                   NaN              NaN                 NaN   

  retrieved_on  
0          NaN  
1          NaN  
2          NaN  
3          NaN  
4          NaN  

[5 rows x 96 columns]

In [250]:
params = {
    'subreddit': 'TheOnion',
    'size': 1000,
    'before': list(theonion_1['retrieved_utc'][-1:])[0] # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

theonion_2 = res.json()
theonion_2 = pd.DataFrame(theonion_2['data'])
print(theonion_2['retrieved_utc'][-1:])
theonion_2.to_csv('./data/theonion_2.csv')
theonion_2.head()

200
999    1660042239
Name: retrieved_utc, dtype: int64


subreddit selftext author_fullname  gilded  \
0  TheOnion                 t2_bdkwy       0   
1  TheOnion              t2_uwxjm0ui       0   
2  TheOnion                 t2_3jamc       0   
3  TheOnion              t2_agfp26zt       0   
4  TheOnion              t2_dm9dhddc       0   

                                               title link_flair_richtext  \
0  Botched Autopsy Brings Murder Victim Back To Life                  []   
1  On Top Of Everything Else, Kevin McCarthy Wett...                  []   
2  On Top Of Everything Else, Kevin McCarthy Wett...                  []   
3  Plume Of Smoke Above Vatican Signals Last Evid...                  []   
4  Species That Had 25 Million Years To Evolve Pa...                  []   

  subreddit_name_prefixed  hidden  pwls link_flair_css_class  ...  \
0              r/TheOnion   False     6                 None  ...   
1              r/TheOnion   False     6                 None  ...   
2              r/TheOnion   False     6                 None  ...   
3              r/TheOnion   False     6                 None  ...   
4              r/TheOnion   False     6                 None  ...   

   updated_utc     utc_datetime_str  crosspost_parent_list  crosspost_parent  \
0   1673138017  2023-01-08 00:33:25                    NaN               NaN   
1   1673124502  2023-01-07 20:48:10                    NaN               NaN   
2   1673032017  2023-01-06 19:06:43                    NaN               NaN   
3   1673026063  2023-01-06 17:27:27                    NaN               NaN   
4   1673017520  2023-01-06 15:05:04                    NaN               NaN   

  author_created_utc  retrieved_on call_to_action gallery_data  is_gallery  \
0                NaN           NaN            NaN          NaN         NaN   
1                NaN           NaN            NaN          NaN         NaN   
2                NaN           NaN            NaN          NaN         NaN   
3                NaN           NaN            NaN          NaN         NaN   
4                NaN           NaN            NaN          NaN         NaN   

  media_metadata  
0            NaN  
1            NaN  
2            NaN  
3            NaN  
4            NaN  

[5 rows x 97 columns]

In [261]:
params = {
    'subreddit': 'TheOnion',
    'size': 1000,
    'before': list(theonion_2['retrieved_utc'][-1:])[0] # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

theonion_3 = res.json()
theonion_3 = pd.DataFrame(theonion_3['data'])
print(theonion_3['retrieved_utc'][-1:])
theonion_3.to_csv('./data/theonion_3.csv')
theonion_3.head()

200
999    1656075153
Name: retrieved_utc, dtype: int64


all_awardings  allow_live_comments  archived     author  author_created_utc  \
0            []                False     False   El_Zarco        1.480668e+09   
1            []                 True     False    Sanlear        1.378417e+09   
2            []                False     False  [deleted]                 NaN   
3            []                 True     False    Sanlear        1.378417e+09   
4            []                False     False  Exastiken        1.339443e+09   

  author_flair_background_color author_flair_css_class author_flair_richtext  \
0                          None                   None                    []   
1                          None                   None                    []   
2                                                 None                   NaN   
3                          None                   None                    []   
4                          None                   None                    []   

  author_flair_template_id author_flair_text  ... wls retrieved_utc  \
0                     None              None  ...   6    1662822928   
1                     None              None  ...   6    1662823312   
2                     None              None  ...   6    1662823428   
3                     None              None  ...   6    1662826214   
4                     None              None  ...   6    1662826885   

  updated_utc     utc_datetime_str gallery_data is_gallery  media_metadata  \
0  1680418419  2022-08-08 20:58:42          NaN        NaN             NaN   
1  1680418015  2022-08-08 16:14:43          NaN        NaN             NaN   
2  1680417893  2022-08-08 14:47:28          NaN        NaN             NaN   
3  1680415195  2022-08-06 17:48:41          NaN        NaN             NaN   
4  1680414532  2022-08-06 06:07:42          NaN        NaN             NaN   

  crosspost_parent crosspost_parent_list  author_cakeday  
0              NaN                   NaN             NaN  
1              NaN                   NaN             NaN  
2              NaN                   NaN             NaN  
3              NaN                   NaN             NaN  
4              NaN                   NaN             NaN  

[5 rows x 97 columns]

In [263]:
params = {
    'subreddit': 'TheOnion',
    'size': 1000,
    'before': list(theonion_3['retrieved_utc'][-1:])[0] # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

theonion_4 = res.json()
theonion_4 = pd.DataFrame(theonion_4['data'])
print(theonion_4['retrieved_utc'][-1:])
theonion_4.to_csv('./data/theonion_4.csv')
theonion_4.head()

200
999    1656103496
Name: retrieved_utc, dtype: int64


all_awardings  allow_live_comments  \
0                                                 []                 True   
1                                                 []                False   
2                                                 []                False   
3  [{'award_sub_type': 'GLOBAL', 'award_type': 'g...                 True   
4                                                 []                 True   

   archived         author  author_created_utc author_flair_background_color  \
0     False        Sanlear        1.378417e+09                          None   
1     False  WorstMedivhKR        1.613751e+09                          None   
2     False        J_LeVeL        1.605582e+09                          None   
3     False    mothershipq        1.293140e+09                          None   
4     False        Sanlear        1.378417e+09                          None   

  author_flair_css_class author_flair_richtext author_flair_template_id  \
0                   None                    []                     None   
1                   None                    []                     None   
2                   None                    []                     None   
3                   None                    []                     None   
4                   None                    []                     None   

  author_flair_text  ...                                                url  \
0              None  ...  https://www.theonion.com/airlines-hiring-anyon...   
1              None  ...  https://www.theonion.com/god-brings-into-exist...   
2              None  ...  https://www.theonion.com/nitro-expected-to-win...   
3              None  ...  https://www.theonion.com/experts-recommend-rai...   
4              None  ...  https://www.theonion.com/indoor-cat-wouldn-t-l...   

                              url_overridden_by_dest view_count  \
0  https://www.theonion.com/airlines-hiring-anyon...       None   
1  https://www.theonion.com/god-brings-into-exist...       None   
2  https://www.theonion.com/nitro-expected-to-win...       None   
3  https://www.theonion.com/experts-recommend-rai...       None   
4  https://www.theonion.com/indoor-cat-wouldn-t-l...       None   

  whitelist_status wls updated_utc     utc_datetime_str crosspost_parent  \
0          all_ads   6  1680345978  2022-06-24 12:50:50              NaN   
1          all_ads   6  1680345249  2022-06-24 00:51:27              NaN   
2          all_ads   6  1680344846  2022-06-23 19:36:19              NaN   
3          all_ads   6  1680344367  2022-06-23 13:28:07              NaN   
4          all_ads   6  1680344156  2022-06-23 10:13:07              NaN   

  crosspost_parent_list  author_cakeday  
0                   NaN             NaN  
1                   NaN             NaN  
2                   NaN             NaN  
3                   NaN             NaN  
4                   NaN             NaN  

[5 rows x 94 columns]

In [264]:
params = {
    'subreddit': 'TheOnion',
    'size': 1000,
    'before': list(theonion_4['retrieved_utc'][-1:])[0] # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

theonion_5 = res.json()
theonion_5 = pd.DataFrame(theonion_5['data'])
print(theonion_5['retrieved_utc'][-1:])
theonion_5.to_csv('./data/theonion_5.csv')
theonion_5.head()

200
999    1656103208
Name: retrieved_utc, dtype: int64


all_awardings  allow_live_comments  \
0  [{'award_sub_type': 'GLOBAL', 'award_type': 'g...                 True   
1                                                 []                False   
2                                                 []                False   
3                                                 []                False   
4                                                 []                False   

   archived              author  author_created_utc  \
0     False  BreakitLikeBeckham        1.537392e+09   
1     False              aresef        1.312772e+09   
2     False              aresef        1.312772e+09   
3     False              aresef        1.312772e+09   
4     False              aresef        1.312772e+09   

  author_flair_background_color author_flair_css_class author_flair_richtext  \
0                          None                   None                    []   
1                          None                   None                    []   
2                          None                   None                    []   
3                          None                   None                    []   
4                          None                   None                    []   

  author_flair_template_id author_flair_text  ...  \
0                     None              None  ...   
1                     None              None  ...   
2                     None              None  ...   
3                     None              None  ...   
4                     None              None  ...   

                                                 url  \
0  https://www.theonion.com/supreme-court-votes-5...   
1  https://www.theonion.com/nation-s-centrists-st...   
2  https://www.theonion.com/anti-abortion-advocat...   
3  https://www.theonion.com/supreme-court-votes-5...   
4  https://www.theonion.com/supreme-court-rules-5...   

                              url_overridden_by_dest view_count  \
0  https://www.theonion.com/supreme-court-votes-5...       None   
1  https://www.theonion.com/nation-s-centrists-st...       None   
2  https://www.theonion.com/anti-abortion-advocat...       None   
3  https://www.theonion.com/supreme-court-votes-5...       None   
4  https://www.theonion.com/supreme-court-rules-5...       None   

  whitelist_status wls updated_utc     utc_datetime_str crosspost_parent  \
0          all_ads   6  1680346601  2022-06-24 20:18:03              NaN   
1          all_ads   6  1680346540  2022-06-24 19:36:10              NaN   
2          all_ads   6  1680346540  2022-06-24 19:35:56              NaN   
3          all_ads   6  1680346540  2022-06-24 19:35:38              NaN   
4          all_ads   6  1680346540  2022-06-24 19:35:24              NaN   

  crosspost_parent_list  author_cakeday  
0                   NaN             NaN  
1                   NaN             NaN  
2                   NaN             NaN  
3                   NaN             NaN  
4                   NaN             NaN  

[5 rows x 94 columns]

In [265]:
params = {
    'subreddit': 'TheOnion',
    'size': 1000,
    'before': list(theonion_5['retrieved_utc'][-1:])[0] # take the UCT integer of your (first....last???) in the dataset to grab the info before that time
    #'after': ???? # takes in a UCT integer
}
res = requests.get(url, params)
print(res.status_code)
res.json()

theonion_6 = res.json()
theonion_6 = pd.DataFrame(theonion_6['data'])
print(theonion_6['retrieved_utc'][-1:])
theonion_6.to_csv('./data/theonion_6.csv')
theonion_6.head()

200
999    1656103208
Name: retrieved_utc, dtype: int64


all_awardings  allow_live_comments  \
0  [{'award_sub_type': 'GLOBAL', 'award_type': 'g...                 True   
1                                                 []                False   
2                                                 []                False   
3                                                 []                False   
4                                                 []                False   

   archived              author  author_created_utc  \
0     False  BreakitLikeBeckham        1.537392e+09   
1     False              aresef        1.312772e+09   
2     False              aresef        1.312772e+09   
3     False              aresef        1.312772e+09   
4     False              aresef        1.312772e+09   

  author_flair_background_color author_flair_css_class author_flair_richtext  \
0                          None                   None                    []   
1                          None                   None                    []   
2                          None                   None                    []   
3                          None                   None                    []   
4                          None                   None                    []   

  author_flair_template_id author_flair_text  ...  \
0                     None              None  ...   
1                     None              None  ...   
2                     None              None  ...   
3                     None              None  ...   
4                     None              None  ...   

                                                 url  \
0  https://www.theonion.com/supreme-court-votes-5...   
1  https://www.theonion.com/nation-s-centrists-st...   
2  https://www.theonion.com/anti-abortion-advocat...   
3  https://www.theonion.com/supreme-court-votes-5...   
4  https://www.theonion.com/supreme-court-rules-5...   

                              url_overridden_by_dest view_count  \
0  https://www.theonion.com/supreme-court-votes-5...       None   
1  https://www.theonion.com/nation-s-centrists-st...       None   
2  https://www.theonion.com/anti-abortion-advocat...       None   
3  https://www.theonion.com/supreme-court-votes-5...       None   
4  https://www.theonion.com/supreme-court-rules-5...       None   

  whitelist_status wls updated_utc     utc_datetime_str crosspost_parent  \
0          all_ads   6  1680346601  2022-06-24 20:18:03              NaN   
1          all_ads   6  1680346540  2022-06-24 19:36:10              NaN   
2          all_ads   6  1680346540  2022-06-24 19:35:56              NaN   
3          all_ads   6  1680346540  2022-06-24 19:35:38              NaN   
4          all_ads   6  1680346540  2022-06-24 19:35:24              NaN   

  crosspost_parent_list  author_cakeday  
0                   NaN             NaN  
1                   NaN             NaN  
2                   NaN             NaN  
3                   NaN             NaN  
4                   NaN             NaN  

[5 rows x 94 columns]

---
# Prior Testing with DadJokes - Learning the API

In [267]:
dad_test = res.json()
dad_test = pd.DataFrame(dad_test['data'])
dad_test

all_awardings  allow_live_comments  \
0    [{'award_sub_type': 'GLOBAL', 'award_type': 'g...                 True   
1                                                   []                False   
2                                                   []                False   
3                                                   []                False   
4                                                   []                False   
..                                                 ...                  ...   
995                                                 []                False   
996                                                 []                False   
997                                                 []                False   
998                                                 []                False   
999                                                 []                False   

     archived              author  author_created_utc  \
0       False  BreakitLikeBeckham        1.537392e+09   
1       False              aresef        1.312772e+09   
2       False              aresef        1.312772e+09   
3       False              aresef        1.312772e+09   
4       False              aresef        1.312772e+09   
..        ...                 ...                 ...   
995     False              Dan-68        1.460838e+09   
996     False               dwaxe        1.246718e+09   
997     False               dwaxe        1.246718e+09   
998     False               dwaxe        1.246718e+09   
999     False               dwaxe        1.246718e+09   

    author_flair_background_color author_flair_css_class  \
0                            None                   None   
1                            None                   None   
2                            None                   None   
3                            None                   None   
4                            None                   None   
..                            ...                    ...   
995                          None                   None   
996                          None                   None   
997                          None                   None   
998                          None                   None   
999                          None                   None   

    author_flair_richtext author_flair_template_id author_flair_text  ...  \
0                      []                     None              None  ...   
1                      []                     None              None  ...   
2                      []                     None              None  ...   
3                      []                     None              None  ...   
4                      []                     None              None  ...   
..                    ...                      ...               ...  ...   
995                    []                     None              None  ...   
996                    []                     None              None  ...   
997                    []                     None              None  ...   
998                    []                     None              None  ...   
999                    []                     None              None  ...   

                                                   url  \
0    https://www.theonion.com/supreme-court-votes-5...   
1    https://www.theonion.com/nation-s-centrists-st...   
2    https://www.theonion.com/anti-abortion-advocat...   
3    https://www.theonion.com/supreme-court-votes-5...   
4    https://www.theonion.com/supreme-court-rules-5...   
..                                                 ...   
995  https://www.theonion.com/comments-that-can-act...   
996  https://www.theonion.com/travis-scott-partners...   
997  https://www.theonion.com/new-york-times-copy-e...   
998  https://www.theonion.com/the-bitter-vend-18480...   
999  https://www.theonion.com/questions-i-get-asked...   

                                url_overridden_by_dest view_coun

In [88]:
dad_jokes_2 = res.json()
dad_jokes_2 = pd.DataFrame(dad_jokes_2['data'])
dad_jokes_2

subreddit                                           selftext  \
0    dadjokes         They told me all their cakes were stollen.   
1    dadjokes                                                      
2    dadjokes     Because they tend to be negative all the time!   
3    dadjokes               And Mayo ”neighs”. \n\n-From my son.   
4    dadjokes  My dad: “I’m gonna get my wife a necklace lock...   
..        ...                                                ...   
994  dadjokes                           Cause he knows is hands.   
995  dadjokes                                          [removed]   
996  dadjokes                  I immediately thought, how dairy.   
997  dadjokes                                         Stypticus.   
998  dadjokes                           They become hummingbirds   

    author_fullname  gilded  \
0       t2_9y3dcase       0   
1          t2_ylyqn       0   
2       t2_30z5q0gm       0   
3       t2_4r7dbrw6       0   
4      t2_7ygzi2hpn       0   
..              ...     ...   
994     t2_d3todswa       0   
995    t2_7xa9h6k3u       0   
996    t2_7gaz1u33s       0   
997     t2_hroo3t49       0   
998     t2_4dh189jr       0   

                                                 title link_flair_richtext  \
0    I went to a German bakery, but I guess they di...                  []   
1    You know what they say about origami - its val...                  []   
2    Why don't scientists trust atoms that are feel...                  []   
3                            I have a horse named Mayo                  []   
4                         A different kind of dad joke                  []   
..                                                 ...                 ...   
994  Wanna know why I’m scared to fight a deaf person?                  []   
995  35[f4M]California states USA looking for a sub...                  []   
996  I saw on a bull calf sucking another mother's ...                  []   
997  What do you call a gladiator who frequently cu...                  []   
998      What happens to birds that can no longer sing                  []   

    subreddit_name_prefixed  hidden  pwls    link_flair_css_class  ...  \
0                r/dadjokes   False     6                    None  ...   
1                r/dadjokes   False     6  post-removed-punchline  ...   
2                r/dadjokes   False     6                    None  ...   
3                r/dadjokes   False     6                    None  ...   
4                r/dadjokes   False     6                    None  ...   
..                      ...     ...   ...                     ...  ...   
994              r/dadjokes   False     6                    None  ...   
995              r/dadjokes   False     6                    None  ...   
996              r/dadjokes   False     6                    None  ...   
997              r/dadjokes   False     6                    None  ...   
998              r/dadjokes   False     6                    None  ...   

     retrieved_utc updated_utc     utc_datetime_str  crosspost_parent_list  \
0       1681095491  1681095491  2023-04-10 02:57:56                    NaN   
1       1681093614  1681093614  2023-04-10 02:26:35                    NaN   
2       1681092188  1681092190  2023-04-10 02:02:57                    NaN   
3       1681090706  1681090706  2023-04-10 01:38:15                    NaN   
4       1681090092  1681090093  2023-04-10 01:27:58                    NaN   
..             ...         ...                  ...                    ...   
994     1680253900  1680253901  2023-03-31 09:11:30                    NaN   
995     1680253043  1680253043  2023-03-31 08:57:05                    NaN   
996     1680248682  1680248683  2023-03-31 07:44:32                    NaN   
997     1680246890  1680246890  2023-03-31 07:14:32                    NaN   
998     1680246697  1680246698  2023-03-31 07:11:21                    NaN   

    url_overridden_by_dest  crosspost_parent post_h

In [36]:
dad_jokes_1 = res.json()
dad_jokes_1 = pd.DataFrame(dad_jokes_1['data'])
dad_jokes_1

subreddit                                      selftext author_fullname  \
0    dadjokes                           Which makes it odd.       t2_16sa6x   
1    dadjokes                     But the music is soulless     t2_81sfkz57   
2    dadjokes                       She broke her calf bone     t2_pjbzysrv   
3    dadjokes      His audience was unresponsive and stiff.    t2_67b2up92p   
4    dadjokes            It's called the Gaga Goo Goo tour.     t2_1i54z8en   
..        ...                                           ...             ...   
994  dadjokes               But they had a great reception.     t2_u7wft8jc   
995  dadjokes                                                     t2_115ne0   
996  dadjokes                                     [removed]     t2_cb8sz8wa   
997  dadjokes                                                   t2_ehylhmzw   
998  dadjokes  She's been giving me nothing but cross words     t2_3o6ndc2i   

     gilded                                              title  \
0         0         2 is the only even number that is a prime.   
1         0  A great pianist died in a hotel and people say...   
2         0                   Why did the cow went to the vet?   
3         0  Why did the mortuary assistant feel his jokes ...   
4         0  Did you know Lady Gaga is touring with The Goo...   
..      ...                                                ...   
994       0  Two TV antenna got married and had a horrible ...   
995       0  I don't usually tell dad jokes... but when I d...   
996       0                               Best Animal Dad Joke   
997       0         Did you know runners don't eat, they fast.   
998       0          My Sudoku addiction is irritating my wife   

    link_flair_richtext subreddit_name_prefixed  hidden  pwls  \
0                    []              r/dadjokes   False     6   
1                    []              r/dadjokes   False     6   
2                    []              r/dadjokes   False     6   
3                    []              r/dadjokes   False     6   
4                    []              r/dadjokes   False     6   
..                  ...                     ...     ...   ...   
994                  []              r/dadjokes   False     6   
995                  []              r/dadjokes   False     6   
996                  []              r/dadjokes   False     6   
997                  []              r/dadjokes   False     6   
998                  []              r/dadjokes   False     6   

       link_flair_css_class  ...  retrieved_utc updated_utc  \
0                      None  ...     1681963327  1681963327   
1                      None  ...     1681962933  1681962934   
2                      None  ...     1681962873  1681962874   
3                      None  ...     1681961506  1681961506   
4                      None  ...     1681960773  1681960773   
..                      ...  ...            ...         ...   
994                    None  ...     1681099140  1681099141   
995  post-removed-punchline  ...     1681098070  1681098070   
996                    None  ...     1681097978  1681097979   
997  post-removed-punchline  ...     1681096568  1681096568   
998                    None  ...     1681096411  1681096412   

        utc_datetime_str  link_flair_template_id post_hint  preview  \
0    2023-04-20 04:01:55                     NaN       NaN      NaN   
1    2023-04-20 03:55:18                     NaN       NaN      NaN   
2    2023-04-20 03:54:23                     NaN       NaN      NaN   
3    2023-04-20 03:31:30                     NaN       NaN      NaN   
4    2023-04-20 03:19:19                     NaN       NaN      NaN   
..                   ...                     ...       ...      ...   
994  2023-04-10 03:58:43                     NaN       NaN      NaN   
995  2023-04-10 03:40:58                     NaN       NaN      NaN   
996  2023-04-10 03:39:25                     NaN       NaN      NaN   
997  2023-04-1